# Домашнее задание 3
## Text Normalization 

deadline: 15 мая 2020, 23:30

В этом домашнем задании вы будете работать с корпусом соревнования по нормализации текстов на русском языке. 

Ссылка на соревнование:
https://www.kaggle.com/c/text-normalization-challenge-russian-language

Корпус (train-test split) доступен там же, на kaggle. Кроме того, kaggle проверяет результаты на тестовом множестве. Пример сабмита в файле: ru_sample_submission_2. 

Задача заключается в том, привести исходный текст (колонку before) в нормализованную форму (колонка after). Дополнительно известны классы токенов (колонка class), общее число классов – 15. В тестовом множестве классы токенов отсутствуют. 

Корпус состоит из предложений на русском языке и их нормализованных аналогов. Примеры продемонстрированы на kaggle.

## ПРАВИЛА
1. Домашнее задание выполняется в группе до 3-х человек.
2. Домашнее задание сдается через anytask, инвайты будут дополнительно высланы.
3. Домашнее задание оформляется в виде отчета либо в .pdf файле, либо ipython-тетрадке. 
4. Отчет должен содержать: нумерацию заданий и пунктов, которые вы выполнили, код решения, и понятное пошаговое описание того, что вы сделали. Отчет должен быть написан в академическом стиле, без излишнего использования сленга и с соблюдением норм русского языка.
5. Не стоит копировать фрагменты лекций, статей и Википедии в ваш отчет.
6. Отчеты, состоящие исключительно из кода, не будут проверены и будут автоматически оценены нулевой оценкой.
7. Плагиат и любое недобросоветсное цитирование приводит к обнуление оценки. 

In [1]:
!pip install kaggle

Could not build wheels for kaggle, since package 'wheel' is not installed.
Could not build wheels for urllib3, since package 'wheel' is not installed.
Could not build wheels for six, since package 'wheel' is not installed.
Could not build wheels for certifi, since package 'wheel' is not installed.
Could not build wheels for python-dateutil, since package 'wheel' is not installed.
Could not build wheels for requests, since package 'wheel' is not installed.
Could not build wheels for tqdm, since package 'wheel' is not installed.
Could not build wheels for python-slugify, since package 'wheel' is not installed.
Could not build wheels for idna, since package 'wheel' is not installed.
Could not build wheels for chardet, since package 'wheel' is not installed.
Could not build wheels for text-unidecode, since package 'wheel' is not installed.


In [1]:
# !pip install kaggle
import os

In [2]:
os.environ['KAGGLE_USERNAME'] = 'darlitlit'
os.environ['KAGGLE_KEY'] = 'dcc30c94bda5fb17c97cc9d0f6c8e407'

In [4]:
!kaggle competitions download -c text-normalization-challenge-russian-language

text-normalization-challenge-russian-language.zip: Skipping, found more recently modified local copy (use --force to force download)


In [17]:
# !unzip text-normalization-challenge-russian-language.zip

## Часть 1. [1 балл] Эксплоративный анализ

1. Найдите примеры каждого класса и опишите, по какой логике проведена нормализация токенов разных классов. 
2. В каких случаях токены класса PLAIN подвергаются нормализации? 
3. Напишите правила для нормализации токенов класса ORDINAL. 

## Часть 2. [6 баллов]  seq2seq архитектуры
Имплементируйте несколько seq2seq архитектур. Энкодер получает на вход последовательность токенов before, декодер учится превращать их в токены after.
Энкодер и декодер работают на уровне символов, эмбеддинги символов инициализируются случайно (по аналогии с работами, в которых предложены нейросетевые модели исправления опечаток).

Эту часть задания рекомендуется выполнять с использованием allennlp (должно быть проще и удобнее).

1. [3 балла] LSTM encoder + LSTM decoder + три механизма внимания: скалярное произведение, аддитивное внимание и мультипликативное внимание (см. лекцию 6, слайд "подсчет весов attention")
2. [3 балла] Transformer

Используя автопровереку kaggle, оцените, как влияют параметры архитектуры на качество задачи.

[бонус] convolutional encoder + convolutional decoder

[бонус] pyramid LSTM (размер l+1 слоя в два раз меньше размера l, i-тый вход l+1 слоя – конкатенация выходов 2i и 2i+1)

## Часть 3. [2 балла]  Дополнительные признаки
Предложите и покажите, как можно было бы повысить качество нейросетевых моделей. Примерные варианты:
1. ансамблирование нейронных сетей
2. добавление морфологоческих признаков 
3. использование эмбеддингов слов 


## Часть 4. [1 балл] Итоги
Напишите краткое резюме проделанной работы. Проведите анализ ошибок: когда модель ошибается? Можно ли скзаать, почему модель ошибается? Сравните результаты всех разработанных моделей. Что помогло вам в выполнении работы, чего не хватало?

# Часть 1. Эксплоративный анализ

1. Найдите примеры каждого класса и опишите, по какой логике проведена нормализация токенов разных классов. 
2. В каких случаях токены класса PLAIN подвергаются нормализации? 
3. Напишите правила для нормализации токенов класса ORDINAL. 

In [29]:
# !pip install tabulate

In [1]:
import os
import numpy as np

import pandas as pd
from tabulate import tabulate

In [2]:
train_df = pd.read_csv('ru_train.csv.zip',  dtype={'before': str, 'after': str})
train_df.before = train_df.before.astype(str)

In [3]:
train_df.head()

sentence_id  token_id  class     before  \
0            0         0  PLAIN         По   
1            0         1  PLAIN  состоянию   
2            0         2  PLAIN         на   
3            0         3   DATE   1862 год   
4            0         4  PUNCT          .   

                                    after  
0                                      По  
1                               состоянию  
2                                      на  
3  тысяча восемьсот шестьдесят второй год  
4                                       .

In [4]:
test_df = pd.read_csv('ru_test.csv.zip',  dtype={'before': str, 'after': str})
test_df.before = test_df.before.astype(str)

In [5]:
test_df.head()

sentence_id  token_id        before
0            0         0  Производится
1            0         1             в
2            0         2          Азии
3            0         3             ,
4            0         4        Африке

In [59]:
test2_df = pd.read_csv('ru_test_2.csv.zip',  dtype={'before': str, 'after': str})
test2_df.before = test2_df.before.astype(str)

In [60]:
test2_df.head()

sentence_id  token_id        before
0            0         0           Эта
1            0         1         книга
2            0         2             ,
3            0         3  отличающаяся
4            0         4             «

In [8]:
examples = pd.read_csv('ru_sample_submission_2.csv.zip')

In [9]:
examples.head()

id         after
0  0_0           Эта
1  0_1         книга
2  0_2             ,
3  0_3  отличающаяся
4  0_4             «

## Найдите примеры каждого класса и опишите, по какой логике проведена нормализация токенов разных классов.

In [7]:
CLS = list(set(train_df['class'].values))

In [51]:
n_examples = 10
for cls in CLS:
    idx = train_df['class'] == cls
    examples = train_df[idx].sample(n_examples)
    print(tabulate(examples[['before', 'after', 'class']],
                   headers=['before', 'after', 'class'],
                   showindex=False))

before    after    class
--------  -------  -------
)         )        PUNCT
,         ,        PUNCT
)         )        PUNCT
.         .        PUNCT
)         )        PUNCT
)         )        PUNCT
«         «        PUNCT
.         .        PUNCT
,         ,        PUNCT
.         .        PUNCT
before    after    class
--------  -------  --------
-         -        VERBATIM
-         -        VERBATIM
Β         бета     VERBATIM
-         -        VERBATIM
-         -        VERBATIM
-         -        VERBATIM
-         -        VERBATIM
-         -        VERBATIM
店        店       VERBATIM
ր         ր        VERBATIM
  before  after                    class
--------  -----------------------  -------
    0185  ноль один восемь пять    DIGIT
      06  ноль шесть               DIGIT
    0941  ноль девять четыре один  DIGIT
      07  ноль семь                DIGIT
      06  ноль шесть               DIGIT
     000  ноль ноль ноль           DIGIT
    0341  ноль три четыре один     DI

before            after                                                                                                        class
----------------  -----------------------------------------------------------------------------------------------------------  ----------
vishime.ru        в_trans и_trans ш_trans и_trans м_trans точка р_trans у_trans                                                ELECTRONIC
tolweb.org        т_trans о_trans л_trans у_trans э_trans б_trans точка о_trans р_trans г_trans                                ELECTRONIC
Shakira.com       ш_trans е_trans й_trans к_trans и_trans р_trans а_trans точка к_trans о_trans м_trans                        ELECTRONIC
OM.net            о_trans м_trans точка н_trans е_trans т_trans                                                                ELECTRONIC
Sportal.bg        с_trans п_trans о_trans р_trans т_trans а_trans л_trans точка b g                                            ELECTRONIC
www.enric.es      w w w точка э_trans н

'PUNCT' -- знаки пунктуация, никак не меняются

'VERBATIM' -- как вслух произносится символ ("в квадрате", "нижнее подчеркивание", буквы греческого алфавита)

'DIGIT' -- числа

'MEASURE' -- как вслух произносятся сокращения для единиц измерения

'TELEPHONE' -- телефон, вместо - ставится sil

'LETTERS' -- пробелом разделяются аббревиатуры

'PLAIN' -- слова, написанные на русском, не меняются, иначе -- транскрибируются

'DECIMAL' -- числа, дробные и с сокращениями (тыс, млн)

'ORDINAL' -- порядковые числительные

'FRACTION' -- дроби

'ELECTRONIC' -- как произносятся ссылки (транскрипция)

'DATE' -- даты

'MONEY' -- числа и валютные названия (транскрипцией, сша -- сэ ш а)

'TIME' -- время

'CARDINAL' -- числа в именительном падеже

## В каких случаях токены класса PLAIN подвергаются нормализации?

In [52]:
plain = train_df[train_df['class'] == 'PLAIN']
plain[plain.before != plain.after].head()

sentence_id  token_id  class     before  \
43             3         7  PLAIN   Tiberius   
44             3         8  PLAIN     Julius   
45             3         9  PLAIN  Pollienus   
46             3        10  PLAIN     Auspex   
153           10         4  PLAIN       Half   

                                                 after  
43   т_trans и_trans б_trans е_trans р_trans и_tran...  
44   д_trans ж_trans у_trans л_trans и_trans у_tran...  
45   п_trans о_trans л_trans л_trans и_trans е_tran...  
46     о_trans с_trans п_trans е_trans к_trans с_trans  
153                    х_trans а_trans л_trans ф_trans

'PLAIN' нормализуются (транслитерируются), если написаны нерусскими буквами

## Напишите правила для нормализации токенов класса ORDINAL

In [64]:
ordinal = train_df[train_df['class'] == 'ORDINAL']
ordinal.head()

sentence_id  token_id    class before                              after
53             3        17  ORDINAL    III                           третьего
163           11         1  ORDINAL   1895   тысяча восемьсот девяносто пятом
164           11         2  ORDINAL  —1896  тысяча восемьсот девяносто шестом
485           35         5  ORDINAL   1796   тысяча семьсот девяносто шестого
487           35         7  ORDINAL   1802            тысяча восемьсот второй

In [65]:
with_ordinals = list(set(ordinal['sentence_id'].values))
with_ordinals = train_df[train_df['sentence_id'].isin(with_ordinals)]

In [74]:
before_df = with_ordinals.groupby(['sentence_id'])['before'].apply(list)
after_df = with_ordinals.groupby(['sentence_id'])['after'].apply(list)

In [76]:
before_df = pd.DataFrame({'text': before_df}).reset_index()
before_df = before_df.text.apply(lambda x: ' '.join(x))

In [84]:
after_df = pd.DataFrame({'text': after_df}).reset_index()
after_df = after_df.text.apply(lambda x: ' '.join(x))

In [87]:
before_df

0        Тиберий Юлий Поллиен Ауспекс ( лат . Tiberius ...
1        в 1895 —1896 годах служил на Черноморском флот...
2        После Павловских реформ , с 1796 по 1802 год ,...
3        Некоторые источники указывают на период 1109 —...
4        Джон Стюарт , 1-й маркиз Бьют , стал носить эт...
                               ...                        
33236    Сформирована 21 апреля 1944 года путем преобра...
33237    Соответственно отодвигался и ввод в прорыв 6-г...
33238    В первом тайме на 7-й минуте Зинедин Зидан реа...
33239    Packard Station Sedan — это легковой автомобил...
33240    В отличие от зенитных артиллерийских полков в ...
Name: text, Length: 33241, dtype: object

## Часть 2. [6 баллов]  seq2seq архитектуры
Имплементируйте несколько seq2seq архитектур. Энкодер получает на вход последовательность токенов before, декодер учится превращать их в токены after.
Энкодер и декодер работают на уровне символов, эмбеддинги символов инициализируются случайно (по аналогии с работами, в которых предложены нейросетевые модели исправления опечаток).

Эту часть задания рекомендуется выполнять с использованием allennlp (должно быть проще и удобнее).

1. [3 балла] LSTM encoder + LSTM decoder + три механизма внимания: скалярное произведение, аддитивное внимание и мультипликативное внимание (см. лекцию 6, слайд "подсчет весов attention")
2. [3 балла] Transformer

Используя автопровереку kaggle, оцените, как влияют параметры архитектуры на качество задачи.

[бонус] convolutional encoder + convolutional decoder

[бонус] pyramid LSTM (размер l+1 слоя в два раз меньше размера l, i-тый вход l+1 слоя – конкатенация выходов 2i и 2i+1)

### LSTM encoder + LSTM decoder + три механизма внимания: скалярное произведение, аддитивное внимание и мультипликативное внимание (см. лекцию 6, слайд "подсчет весов attention")

Скалярное произведение -- allennlp.modules.attention.dot_product_attention.DotProductAttention


Аддитивное внимание -- allennlp.modules.attention.additive_attention.AdditiveAttention


Мультипликативное внимание -- allennlp.modules.attention.bilinear_attention.BilinearAttention

In [10]:
# !pip install allennlp

In [1]:
from allennlp.modules.seq2seq_encoders import Seq2SeqEncoder, PytorchSeq2SeqWrapper
from allennlp.models.encoder_decoders.simple_seq2seq import SimpleSeq2Seq
from allennlp.predictors import SimpleSeq2SeqPredictor
from allennlp.modules.attention import LinearAttention
from allennlp.nn.activations import Activation
from allennlp.data.tokenizers.character_tokenizer import CharacterTokenizer
from allennlp.data.vocabulary import Vocabulary
from allennlp.data.dataset_readers import DatasetReader
from allennlp.data.token_indexers import TokenCharactersIndexer
from allennlp.data.token_indexers import TokenIndexer, SingleIdTokenIndexer
from allennlp.data.tokenizers import Token
from allennlp.data.fields import TextField, SequenceLabelField
from allennlp.data import Instance
from allennlp.modules.text_field_embedders import TextFieldEmbedder, BasicTextFieldEmbedder
from allennlp.modules.token_embedders import Embedding
from allennlp.training.metrics import CategoricalAccuracy
from allennlp.data.iterators import BucketIterator
from allennlp.training.trainer import Trainer
from allennlp.data.dataset_readers.seq2seq import Seq2SeqDatasetReader
from allennlp.modules.attention import LinearAttention, BilinearAttention, DotProductAttention, AdditiveAttention
from allennlp.modules.seq2seq_encoders import StackedSelfAttentionEncoder
from allennlp.data.tokenizers.word_tokenizer import WordTokenizer
from allennlp.data.tokenizers.token import Token
from allennlp.data.tokenizers.word_splitter import WordSplitter
from allennlp.data.tokenizers.tokenizer import Tokenizer

import torch

import torch.optim as optim
import pandas as pd

from typing import List

from overrides import overrides

from tqdm.notebook import tqdm_notebook as tqdm

from sklearn.model_selection import train_test_split

import pickle

import itertools

In [2]:
CUDA_DEVICE = torch.cuda.current_device()

In [3]:
assert torch.cuda.device_count() > 0

### Seq2Seq Подход 1 -- CharEmbedding по предложениям

Первым нашим подходом было взять предложения, и токенизировать по символам (как написано в задании)

Подход не оправдал себя по двум причинам:
1. Требуется очень много эпох, чтобы seq2seq начал предсказывать что-то адекватное
2. Все попытки восстановить ответ (в ответе нужен итоговый токен для каждого исходного) не обвенчались успехом

В терминах allenlp: предложение -- $Instance$, символы (или БУКВА_trans) -- $Token$

In [10]:
# Функция, которая группирует исходные данные по sentence_id

def group_by_sentence(df: pd.DataFrame):
    new_df = pd.DataFrame(columns=['before', 'after'])
    groupped = df.groupby(['sentence_id'])
    new_df['after'] = groupped['after'].apply(lambda x: ' '.join(x))
    new_df['before'] = groupped['before'].apply(lambda x: ' '.join(x))

    return new_df

In [16]:
group_by_sentence(train_df.head(1000))

before  \
sentence_id                                                      
0                                   По состоянию на 1862 год .   
1            Оснащались латными рукавицами и сабатонами с н...   
2            В конце 1811 года , вследствие конфликта с про...   
3            Тиберий Юлий Поллиен Ауспекс ( лат . Tiberius ...   
4            Севернее Дудинки и северо - восточнее Белочи ,...   
...                                                        ...   
67           Джон Стюарт , 1-й маркиз Бьют , стал носить эт...   
68           На Плоском Мире восьмисторонняя призма способн...   
69           В 2011 вышел четвертый альбом , Je suis , в 20...   
70           Агатовая Империя занимает почти весь Противове...   
71           Арис представлял себя населению в качестве « м...   

                                                         after  
sentence_id                                                     
0            По состоянию на тысяча восемьсот шестьдесят вт...  
1            Оснащались латными рукавицами и сабатонами с н...  
2            В конце тысяча восемьсот одиннадцатого года , ...  
3            Тиберий Юлий Поллиен Ауспекс ( лат . т_trans и...  
4            Севернее Дудинки и северо - восточнее Белочи ,...  
...                                                        ...  
67           Джон Стюарт , первый маркиз Бьют , стал носить...  
68           На Плоском Мире восьмисторонняя призма способн...  
69           В двух тысячах одиннадцати вышел четвертый аль...  
70           Агатовая Империя занимает почти весь Противове...  
71           Арис представлял себя населению в качестве « м...  

[72 rows x 2 columns]

In [17]:
train_df_groupped = group_by_sentence(train_df)

In [19]:
with open('train_df_groupped.pickle', 'wb') as f:
    pickle.dump(train_df_groupped, f)

In [29]:
with open('train_df_groupped.pickle', 'rb') as f:
    train_df_groupped = pickle.load(f)

In [12]:
len(train_df_groupped[train_df_groupped['before'] != train_df_groupped['after']]), len(train_df_groupped)

(438263, 761436)

Удаляем из обучения предложения с одинаковыми before и after, а также слишком длинные

In [13]:
train_cut = train_df_groupped[train_df_groupped['before'] != train_df_groupped['after']]
train_cut = train_cut[train_cut['before'].apply(len) < 500]
train_cut = train_cut[train_cut['after'].apply(len) < 500]

In [14]:
len(train_cut)

427943

In [15]:
_X_train, _X_test = train_test_split(train_cut, test_size=0.1, random_state=42)


In [16]:
_X_pretrain = _X_train.copy()
_X_pretrain.after = _X_pretrain.before

In [18]:
sorted(train_cut.before.apply(len))[-10:]

[336, 346, 354, 359, 382, 397, 404, 412, 438, 473]

Сохраняем данные в две колонки -- before, after. Такой формат требует Seq2SeqDatasetReader

Pretrain -- это данные для предобучения. Трюк взят из статьи про seq2seq
https://guillaumegenthial.github.io/sequence-to-sequence.html
>To speedup things, one trick is to feed the actual output sequence (<sos> comment vas tu) into the decoder’s LSTM and predict the next token at every position (comment vas tu <eos>).
    
A <sos\> и <eos\> добавляются при чтении, см start_tokens, end_tokens

Таким образом, в обучении, есть две стадии:
1. pretrain:
    
   В этом случае target является  копией before, но со сдвигом
    
   Таким образом seq2seq учится угадывать следующее слово 
2. train:
    
    По уже предобученной модели учим финальное предсказание

In [113]:
_X_pretrain.to_csv('X_pretrain_allennlp.tsv', sep='\t', header=False, columns=['before', 'after'], index=False)
_X_train.to_csv('X_train_allennlp.tsv', sep='\t', header=False, columns=['before', 'after'], index=False)
_X_test.to_csv('X_test_allennlp.tsv', sep='\t', header=False, columns=['before', 'after'], index=False)

**CharacterWithTransWordSplitter** нужен для того, чтобы подать его на вход в WordTokenizer.
Он делает так, чтобы токенами были символы, кроме случая с a_trans, к_trans и т.п., -- они преобразуются в отдельные токены

In [5]:
@WordSplitter.register('character_with_trans')
class CharacterWithTransWordSplitter(WordSplitter):
    """
    A ``WordSplitter`` that convert string to characters except of a_trans b_trans and so on cases
    """
    def __init__(
        self,
        use_trans_tokens=True, 
        lowercase_characters: bool = False
    ) -> None:
        self._use_trans_tokens = use_trans_tokens
        self._lowercase_characters = lowercase_characters
    
    @overrides
    def batch_split_words(self, sentences: List[str]) -> List[List[Token]]:
        return [self.split_words(setence)
                for sentence in sentences]
    
    def _sanitize(self, sentence: List[str]) -> List[Token]:
        return list(map(Token, sentence))

    @overrides
    def split_words(self, sentence: str) -> List[Token]:
        # This works because our Token class matches spacy's.
        if self._lowercase_characters:
            sentence = sentence.lower()
        words = sentence.split(' ')
        out = []
        for word in words:
            if self._use_trans_tokens and word.endswith('trans'):
                out.append(word)
            else:
                out += list(word)
            out.append(' ')
        out.pop()
        
        return self._sanitize(out)

In [17]:
source_token_indexer =  {
    'tokens': SingleIdTokenIndexer(namespace='tokens')
}
target_token_indexer =  {
    'tokens': SingleIdTokenIndexer(namespace='target_tokens')
}

source_tokenizer = WordTokenizer(
    word_splitter=CharacterWithTransWordSplitter(lowercase_characters=False), 
    end_tokens=['<eos>'],
)
target_tokenizer = WordTokenizer(
    word_splitter=CharacterWithTransWordSplitter(lowercase_characters=False),
    start_tokens=['<sos>'],
)
reader = Seq2SeqDatasetReader(
        source_tokenizer=source_tokenizer,
        target_tokenizer=target_tokenizer,
        source_token_indexers=source_token_indexer,
        target_token_indexers=target_token_indexer,
#         lazy=True # позволяет не поднимать датасет в память
)
X_train = reader.read('X_train_allennlp.tsv')
X_pretrain = reader.read('X_pretrain_allennlp.tsv')
X_test = reader.read('X_test_allennlp.tsv')
# X_train = reader.read('X_train_allennlp_10000.tsv')
# X_pretrain = reader.read('X_pretrain_allennlp_10000.tsv')
# X_test = reader.read('X_test_allennlp_10000.tsv')

385148it [02:38, 2425.98it/s]
385148it [02:00, 3185.42it/s]
42795it [00:07, 5392.10it/s]


In [5]:
print(X_pretrain[2])

Instance with fields:
 	 source_tokens: TextField of length 85 with text: 
 		[@start@, Р, а, б, о, т, а, м, и,  , р, у, к, о, в, о, д, и, л, и,  , А, .,  , И, .,  , С, о, к, о,
		л, о, в,  , и,  , е, г, о,  , з, а, м, е, с, т, и, т, е, л, и,  , Г, .,  , А, .,  , Т, ю, л, и, н,
		, и,  , Ю, .,  , А, .,  , М, о, з, ж, о, р, и, н,  , ., <eos>, @end@]
 		and TokenIndexers : {'tokens': 'SingleIdTokenIndexer'} 
 	 target_tokens: TextField of length 85 with text: 
 		[@start@, <sos>, Р, а, б, о, т, а, м, и,  , р, у, к, о, в, о, д, и, л, и,  , А, .,  , И, .,  , С, о,
		к, о, л, о, в,  , и,  , е, г, о,  , з, а, м, е, с, т, и, т, е, л, и,  , Г, .,  , А, .,  , Т, ю, л,
		и, н,  , и,  , Ю, .,  , А, .,  , М, о, з, ж, о, р, и, н,  , ., @end@]
 		and TokenIndexers : {'tokens': 'SingleIdTokenIndexer'} 



In [106]:
print(X_test[2])

Instance with fields:
 	 source_tokens: TextField of length 96 with text: 
 		[@start@, «,  , К, р, а, с, н, о,  , -,  , ч, е, р, н, ы, е,  , »,  , п, р, о, п, у, с, т, и, л, и,
		, 1, 2,  , г, о, л, о, в,  , ,,  , 4,  , и, з,  , н, и, х,  , б, ы, л, и,  , п, р, о, п, у, щ, е, н,
		ы,  , в,  , о, т, с, у, т, с, т, в, и, и,  , Д, ж, о, н, а,  , н, а,  , п, о, л, е,  , ., @end@]
 		and TokenIndexers : {'tokens': 'SingleIdTokenIndexer'} 
 	 target_tokens: TextField of length 109 with text: 
 		[@start@, «,  , К, р, а, с, н, о,  , -,  , ч, е, р, н, ы, е,  , »,  , п, р, о, п, у, с, т, и, л, и,
		, д, в, е, н, а, д, ц, а, т, ь,  , г, о, л, о, в,  , ,,  , ч, е, т, ы, р, е,  , и, з,  , н, и, х,  ,
		б, ы, л, и,  , п, р, о, п, у, щ, е, н, ы,  , в,  , о, т, с, у, т, с, т, в, и, и,  , Д, ж, о, н, а,
		, н, а,  , п, о, л, е,  , ., @end@]
 		and TokenIndexers : {'tokens': 'SingleIdTokenIndexer'} 



In [5]:
vocab = Vocabulary.from_instances(X_train + X_test,
                                  min_count={'source_tokens': 10,
                                             'target_tokens': 10})

100%|██████████| 20000/20000 [00:02<00:00, 8910.14it/s]


In [24]:
vocab

Vocabulary with namespaces:  target_tokens, Size: 391 || tokens, Size: 2180 || Non Padded Namespaces: {'*labels', '*tags'}

In [6]:
VOCAB_DIR = "vocabulary"

In [8]:

vocab.save_to_files(VOCAB_DIR)

In [7]:
vocab = Vocabulary.from_files(VOCAB_DIR)

In [66]:
vocab.get_vocab_size('tokens')

37964

Задаем большинство параметров по умолчанию

In [14]:
CUDA_DEVICE = 0
CUDA_DEVICES = [0, 1]
EN_EMBEDDING_DIM = 256
HIDDEN_DIM = 256
max_decoding_steps = 10
ZH_EMBEDDING_DIM = 256

In [16]:
# нужно для многократного запуска, чтобы torch освободил память на карточке

try:
    del model
except:
    pass

try:
    del trainer
except:
    pass
try:
    del pretrainer
except:
    pass
    

torch.cuda.empty_cache()

In [538]:
def get_model(*, vocab):
    en_embedding = Embedding(num_embeddings=vocab.get_vocab_size('tokens'),
                             embedding_dim=EN_EMBEDDING_DIM)
    encoder = PytorchSeq2SeqWrapper(
        torch.nn.LSTM(EN_EMBEDDING_DIM, HIDDEN_DIM, batch_first=True))
    #encoder = StackedSelfAttentionEncoder(input_dim=EN_EMBEDDING_DIM, hidden_dim=HIDDEN_DIM, projection_dim=128, feedforward_hidden_dim=128, num_layers=1, num_attention_heads=8)

    source_embedder = BasicTextFieldEmbedder({"tokens": en_embedding})

    # attention = BilinearAttention(HIDDEN_DIM, HIDDEN_DIM)
    attention = DotProductAttention()

    max_decoding_steps = 400
    model = SimpleSeq2Seq(vocab, source_embedder, encoder, max_decoding_steps,
                          target_embedding_dim=ZH_EMBEDDING_DIM,
                          target_namespace='target_tokens',
                          attention=attention,
                          beam_size=8,
                          use_bleu=True)
    model.cuda(CUDA_DEVICE)
    
    return model


def get_trainer(*, model, X_train, X_test):
   
    optimizer = optim.Adam(model.parameters())
    iterator = BucketIterator(batch_size=1024, sorting_keys=[("source_tokens", "num_tokens")])

    iterator.index_with(vocab)

    trainer = Trainer(model=model,
                      optimizer=optimizer,
                      iterator=iterator,
                      train_dataset=X_train,
                      validation_dataset=X_test,
                      num_epochs=1,  # 1 потому что несколько эпох запускается в run_trainer
                      cuda_device=CUDA_DEVICES)

    return trainer

def run_trainer(*, model,  trainer, epochs):
    for i in range(epochs):
        print('Epoch: {}'.format(i))
        trainer.train()

        predictor = SimpleSeq2SeqPredictor(model, reader)

        for instance in itertools.islice(X_test, 10):
            print('SOURCE:', ''.join(map(str, instance.fields['source_tokens'].tokens)))
            print('GOLD:', ''.join(map(str, instance.fields['target_tokens'].tokens)))
            print('PRED:', ''.join(map(str, predictor.predict_instance(instance)['predicted_tokens'])))
        print()
    return trainer

In [9]:
model = get_model(vocab=vocab)

In [10]:
pretrainer = get_trainer(model=model, X_train=X_pretrain, X_test=X_test[:100])
run_trainer(model=model, trainer=pretrainer, epochs=200)

You provided a validation dataset but patience was set to None, meaning that early stopping is disabled


Epoch: 0


loss: 3.9665 ||: 100%|██████████| 48/48 [03:25<00:00,  4.29s/it]  
BLEU: 0.0000, loss: 3.7895 ||: 100%|██████████| 1/1 [00:05<00:00,  5.16s/it]


SOURCE: @start@Проходило 25 октября 2009 года на « Сивик - арене » в Питтсбурге , Пенсильвания .<eos>@end@
GOLD: @start@<sos>Проходило двадцать пятого октября две тысячи девятого года на « Сивик - арене » в Питтсбурге , Пенсильвания .@end@
PRED: <sos>В                                                                                                                                                                                                                                                                                                                                                                                                              
SOURCE: @start@8 в . ( от 9 — 8 вв . ) — Возникновение греческого алфавита .<eos>@end@
GOLD: @start@<sos>восемь в . ( от девять до восемь в в . ) — Возникновение греческого алфавита .@end@
PRED: <sos>В                                                                                                                                                    

loss: 3.3434 ||: 100%|██████████| 48/48 [01:42<00:00,  2.14s/it]
BLEU: 0.0000, loss: 3.2058 ||: 100%|██████████| 1/1 [00:05<00:00,  5.39s/it]


...

SOURCE: @start@Проходило 25 октября 2009 года на « Сивик - арене » в Питтсбурге , Пенсильвания .<eos>@end@
GOLD: @start@<sos>Проходило двадцать пятого октября две тысячи девятого года на « Сивик - арене » в Питтсбурге , Пенсильвания .@end@
PRED: <sos>Проходило 25 октября 2011 ) .
SOURCE: @start@8 в . ( от 9 — 8 вв . ) — Возникновение греческого алфавита .<eos>@end@
GOLD: @start@<sos>восемь в . ( от девять до восемь в в . ) — Возникновение греческого алфавита .@end@
PRED: <sos>8 в . ( от 9 — 1998 . Архивирование протительского поставляет в составляет .
SOURCE: @start@« Красно - черные » пропустили 12 голов , 4 из них были пропущены в отсутствии Джона на поле .<eos>@end@
GOLD: @start@<sos>« Красно - черные » пропустили двенадцать голов , четыре из них были пропущены в отсутствии Джона на поле .@end@
PRED: <sos>« Красно - человерского из первоисточника 2013 . Архивировано из первоисточника 2011 года .
SOURCE: @start@Проверено 27 мая 2012 . Архивировано из первоисточника 23 сентября 2012 .

loss: 1.6230 ||: 100%|██████████| 48/48 [01:40<00:00,  2.09s/it]
BLEU: 0.1220, loss: 3.1180 ||: 100%|██████████| 1/1 [00:05<00:00,  5.15s/it]


SOURCE: @start@Проходило 25 октября 2009 года на « Сивик - арене » в Питтсбурге , Пенсильвания .<eos>@end@
GOLD: @start@<sos>Проходило двадцать пятого октября две тысячи девятого года на « Сивик - арене » в Питтсбурге , Пенсильвания .@end@
PRED: <sos>Проходило 25 октября 2012 ) .
SOURCE: @start@8 в . ( от 9 — 8 вв . ) — Возникновение греческого алфавита .<eos>@end@
GOLD: @start@<sos>восемь в . ( от девять до восемь в в . ) — Возникновение греческого алфавита .@end@
PRED: <sos>8 в . ( от 9 — 1978 . Архивирование предительственный компании .
SOURCE: @start@« Красно - черные » пропустили 12 голов , 4 из них были пропущены в отсутствии Джона на поле .<eos>@end@
GOLD: @start@<sos>« Красно - черные » пропустили двенадцать голов , четыре из них были пропущены в отсутствии Джона на поле .@end@
PRED: <sos>« Красно - черника в составляется в составляется в составляется в составляется в составляется в составляется в составляется .
SOURCE: @start@Проверено 27 мая 2012 . Архивировано из первоисточн

loss: 1.6020 ||: 100%|██████████| 48/48 [01:40<00:00,  2.09s/it]
BLEU: 0.1369, loss: 3.1232 ||: 100%|██████████| 1/1 [00:05<00:00,  5.46s/it]


SOURCE: @start@Проходило 25 октября 2009 года на « Сивик - арене » в Питтсбурге , Пенсильвания .<eos>@end@
GOLD: @start@<sos>Проходило двадцать пятого октября две тысячи девятого года на « Сивик - арене » в Питтсбурге , Пенсильвания .@end@
PRED: <sos>Проходило 25 октября 2012 ) .
SOURCE: @start@8 в . ( от 9 — 8 вв . ) — Возникновение греческого алфавита .<eos>@end@
GOLD: @start@<sos>восемь в . ( от девять до восемь в в . ) — Возникновение греческого алфавита .@end@
PRED: <sos>8 в . ( от 19 — 1978 . Архивирование призверской компании в 1945 года .
SOURCE: @start@« Красно - черные » пропустили 12 голов , 4 из них были пропущены в отсутствии Джона на поле .<eos>@end@
GOLD: @start@<sos>« Красно - черные » пропустили двенадцать голов , четыре из них были пропущены в отсутствии Джона на поле .@end@
PRED: <sos>« Красно - черный компания , в составляет в составляется в составляет в составляется в составляется в составляется в составляется в составляется .
SOURCE: @start@Проверено 27 мая 2012 .

In [11]:
trainer = get_trainer(model=model, X_train=X_train, X_test=X_test[:100])
run_trainer(model=model, trainer=trainer, epochs=200)

You provided a validation dataset but patience was set to None, meaning that early stopping is disabled


Epoch: 0


loss: 1.7768 ||: 100%|██████████| 48/48 [05:24<00:00,  6.76s/it]  
BLEU: 0.1393, loss: 1.4236 ||: 100%|██████████| 1/1 [00:05<00:00,  5.23s/it]


SOURCE: @start@Проходило 25 октября 2009 года на « Сивик - арене » в Питтсбурге , Пенсильвания .<eos>@end@
GOLD: @start@<sos>Проходило двадцать пятого октября две тысячи девятого года на « Сивик - арене » в Питтсбурге , Пенсильвания .@end@
PRED: <sos>Проходило года .
SOURCE: @start@8 в . ( от 9 — 8 вв . ) — Возникновение греческого алфавита .<eos>@end@
GOLD: @start@<sos>восемь в . ( от девять до восемь в в . ) — Возникновение греческого алфавита .@end@
PRED: <sos>дев . ) .
SOURCE: @start@« Красно - черные » пропустили 12 голов , 4 из них были пропущены в отсутствии Джона на поле .<eos>@end@
GOLD: @start@<sos>« Красно - черные » пропустили двенадцать голов , четыре из них были пропущены в отсутствии Джона на поле .@end@
PRED: <sos>« Красного года .
SOURCE: @start@Проверено 27 мая 2012 . Архивировано из первоисточника 23 сентября 2012 . Кодваль ( фр . ) .<eos>@end@
GOLD: @start@<sos>Проверено двадцать седьмого мая две тысячи двенадцатого года . Архивировано из первоисточника двадцать тре

loss: 1.3453 ||: 100%|██████████| 48/48 [04:03<00:00,  5.08s/it]
BLEU: 0.1005, loss: 1.2894 ||: 100%|██████████| 1/1 [00:05<00:00,  5.54s/it]


...

SOURCE: @start@Проходило 25 октября 2009 года на « Сивик - арене » в Питтсбурге , Пенсильвания .<eos>@end@
GOLD: @start@<sos>Проходило двадцать пятого октября две тысячи девятого года на « Сивик - арене » в Питтсбурге , Пенсильвания .@end@
PRED: <sos>Проходило двадцать седьмого января две тысячи тринадцатого года . « Советственность на процентов , поставляется в тысяча девятьсот шестьдесят седьмого года , поставляется в тысяча девятьсот пятьдесят седьмом году .
SOURCE: @start@8 в . ( от 9 — 8 вв . ) — Возникновение греческого алфавита .<eos>@end@
GOLD: @start@<sos>восемь в . ( от девять до восемь в в . ) — Возникновение греческого алфавита .@end@
PRED: <sos>восемнадцатое апреля тысяча восемьсот восемьдесят втором году вв . ) — тысяча восемьсот восемьдесят второго года .
SOURCE: @start@« Красно - черные » пропустили 12 голов , 4 из них были пропущены в отсутствии Джона на поле .<eos>@end@
GOLD: @start@<sos>« Красно - черные » пропустили двенадцать голов , четыре из них были пропущены в 

loss: 0.8756 ||: 100%|██████████| 48/48 [04:04<00:00,  5.08s/it]
BLEU: 0.3695, loss: 0.8279 ||: 100%|██████████| 1/1 [00:07<00:00,  7.75s/it]


SOURCE: @start@Проходило 25 октября 2009 года на « Сивик - арене » в Питтсбурге , Пенсильвания .<eos>@end@
GOLD: @start@<sos>Проходило двадцать пятого октября две тысячи девятого года на « Сивик - арене » в Питтсбурге , Пенсильвания .@end@
PRED: <sos>Проходило двадцать седьмого ноября две тысячи тринадцатого года . « составительность населенного составителенного составительного составительного составительности .
SOURCE: @start@8 в . ( от 9 — 8 вв . ) — Возникновение греческого алфавита .<eos>@end@
GOLD: @start@<sos>восемь в . ( от девять до восемь в в . ) — Возникновение греческого алфавита .@end@
PRED: <sos>восемнадцатое апреля тысяча девятьсот восемьдесят восьмого года , тысяча восемьсот восемьдесят две тысячи восемьсот восемьдесят восемьсот восемьдесят восемь . — две тысячи восемьсот восемьдесят девятого года .
SOURCE: @start@« Красно - черные » пропустили 12 голов , 4 из них были пропущены в отсутствии Джона на поле .<eos>@end@
GOLD: @start@<sos>« Красно - черные » пропустили двена

loss: 1.2722 ||: 100%|██████████| 48/48 [04:04<00:00,  5.09s/it]
BLEU: 0.2457, loss: 1.0690 ||: 100%|██████████| 1/1 [00:05<00:00,  5.64s/it]


SOURCE: @start@Проходило 25 октября 2009 года на « Сивик - арене » в Питтсбурге , Пенсильвания .<eos>@end@
GOLD: @start@<sos>Проходило двадцать пятого октября две тысячи девятого года на « Сивик - арене » в Питтсбурге , Пенсильвания .@end@
PRED: <sos>Проходило четырнадцать восемьдесят одиннадцать восемьдесят одиннадцать восемь sil две тысячи девятьсот девяносто восемьдесят восемьдесят одиннадцать семьдесят двадцать четыре — тысяча девятьсот двадцать четыре — тысяча девятьсот двадцать четыре — тысяча девятьсот двадцать четыре — тысяча девятьсот двадцать четыре — тысяча девятьсот двадцать пятого года .
SOURCE: @start@8 в . ( от 9 — 8 вв . ) — Возникновение греческого алфавита .<eos>@end@
GOLD: @start@<sos>восемь в . ( от девять до восемь в в . ) — Возникновение греческого алфавита .@end@
PRED: <sos>в тысяча девятьсот девяносто восемьдесят двадцать четвертого восемьдесят одиннадцать четыре — тысяча девятьсот двадцать четыре — тысяча девятьсот двадцать четыре — тысяча девятьсот девяносто в

In [12]:
with open("./models/simple_sentence_lstm_200epochs/simple_sentence_lstm_200epochs.th", 'wb') as f:
    torch.save(model.state_dict(), f)

Итог -- предикшны странные, как токенизировать их и сделать в формате сдачи в kaggle, непонятно
Максимальный BLEU -- порядка 0.4, что достаточно плохо

### Подход 2 -- Оставляем только окошки того, что надо предсказывать

Идея такая -- если есть токен, который (как ожидается) должен измениться после преобразования seq2seq, то мы в качестве входа берем этот токен и <<окно>> по несколько токенов влево и вправо. А в качестве ответа преобразовнное окно

Код мы написали до того, как посмотрели формат сдачи (пока обучался вариант с предложениями), но обучать не пробовали, потому что, как и в предыдущем варианте, непонятно как ответ восстановить по токенам

In [6]:
source_tokenizer = WordTokenizer(
    word_splitter=CharacterWithTransWordSplitter(lowercase_characters=False), 
    end_tokens=['<eos>'],
)
target_tokenizer = WordTokenizer(
    word_splitter=CharacterWithTransWordSplitter(lowercase_characters=False),
    start_tokens=['<sos>'],
)
source_token_indexer =  {
    'tokens': SingleIdTokenIndexer(namespace='tokens')
}
target_token_indexer =  {
    'tokens': SingleIdTokenIndexer(namespace='target_tokens')
}
reader = Seq2SeqDatasetReader(
    source_tokenizer=source_tokenizer,
    target_tokenizer=target_tokenizer,
    source_token_indexers=source_token_indexer,
    target_token_indexers=target_token_indexer,
#         lazy=True
)
# X_train = reader.read('X_train_allennlp.tsv')
# X_pretrain = reader.read('X_pretrain_allennlp.tsv')
# X_test = reader.read('X_test_allennlp.tsv')
X_train = reader.read('X_train_allennlp_10000.tsv')
X_pretrain = reader.read('X_pretrain_allennlp_10000.tsv')
X_test = reader.read('X_test_allennlp_10000.tsv')

10000it [00:03, 2520.10it/s]
10000it [00:03, 2904.89it/s]
10000it [00:04, 2439.40it/s]


In [17]:
print(''.join(map(str, X_train[0]['source_tokens'])))
print(''.join(map(str, X_train[0]['target_tokens'])))

@start@Получил статус села ( Pueblo ) 19 августа 1926 года .<eos>@end@
@start@<sos>Получил статус села ( п_trans у_trans э_trans б_trans л_trans о_trans ) девятнадцатого августа тысяча девятьсот двадцать шестого года .@end@


Напишем процессинг предложений

Процессинг устроен следующим образом -- берем участки, где токены before не равны токенам в after
от таких участков берем **left_window_size** токенов слева и **right_windiw_size** токенов справа

Причем если есть пересекающиеся такие кусочки, их склеиваем.

Опционально (**_add_unchanged**) все пропущенные токены тоже оставляем, но добавляем пометку -- $different == False$

В итоге предложения разбиваются на непересекающиеся куски (окна), где
- **different == True** можно подавать на вход Trainer.
- **different = False** в предикте используем как неизмененную часть


In [20]:
import re

In [21]:
class WindowMaker:
    need_transform_regex = re.compile('[A-Za-z0-9]')
    
    def __init__(
        self,
        add_unchanged=False,
        left_window_size=2, 
        right_window_size=2,
    ):
        self._add_unchanged = add_unchanged
        self._left_window_size = left_window_size
        self._right_window_size = right_window_size
    
    def __call__(
        self, 
        df: pd.DataFrame,
        mode='train',
    ) -> pd.DataFrame:
        groupped = df.groupby(['sentence_id'])
        return groupped.apply(lambda x: self._process_sentence(x, mode))
    
    def _need_transform(self, a, b, mode):
        if mode == 'train':
            return a != b
        upcase_cnt = sum(1 for c in a if c.isupper())
        if upcase_cnt > 2:
            return True
        if WindowMaker.need_transform_regex.search(a):
            return True
        return False
    
    def _process_sentence(self, df: pd.DataFrame, mode) -> pd.DataFrame:
        new_before = []
        new_after = []

        before = df.before.to_list()
        if mode == 'test':
            after = before
        else:
            after = df.after.to_list()
        assert len(before) == len(after)
        i = 0
        different = []
        left_window_idx = 0
        right_window_idx = 0
        while i < len(before):
            start_window = i
            while i < len(before) and not self._need_transform(before[i], after[i], mode):
                i += 1
                
            left_window_idx = max(0, i - self._left_window_size)
            any_dirretent = False
            while i < len(before) and self._need_transform(before[i], after[i], mode):
                any_dirretent = True
                i += 1
                
            right_window_idx = min(len(before), i + self._right_window_size)
            
            
            if not any_dirretent:
                left_window_idx = right_window_idx = i
            
            i = right_window_idx
            
            if self._add_unchanged and start_window < left_window_idx:
                new_before.append(' '.join(before[start_window:left_window_idx]))
                new_after.append(' '.join(after[start_window:left_window_idx]))
                different.append(False)
                
            if any_dirretent:
                new_before.append(' '.join(before[left_window_idx:right_window_idx]))
                new_after.append(' '.join(after[left_window_idx:right_window_idx]))
                different.append(True)
        if self._add_unchanged:
            return pd.DataFrame({
                'before': new_before, 
                'after': new_after,
                'different': different,
            })
        return pd.DataFrame({
            'before': new_before, 
            'after': new_after,
        })
            

In [31]:
WindowMaker(add_unchanged=False)(train_df.head(100))

before  \
sentence_id                                                 
0           0                     состоянию на 1862 год .   
2           0              В конце 1811 года , вследствие   
3           0  лат . Tiberius Julius Pollienus Auspex ) —   
            1                   деятель начала III века .   
6           0    Проверено 12 февраля 2013 . Архивировано   
            1      из первоисточника 15 февраля 2013 . TV   

                                                           after  
sentence_id                                                       
0           0  состоянию на тысяча восемьсот шестьдесят второ...  
2           0  В конце тысяча восемьсот одиннадцатого года , ...  
3           0  лат . т_trans и_trans б_trans е_trans р_trans ...  
            1                     деятель начала третьего века .  
6           0  Проверено двенадцатого февраля две тысячи трин...  
            1  из первоисточника пятнадцатого февраля две тыс...

Проверим, что никакие кусочки не были потеряны:

In [35]:
def test():
    # группируем исходные данные
    df1 = group_by_sentence(train_df.head(100))
    # группироуем окошки
    df2 = group_by_sentence(WindowMaker(add_unchanged=True)(train_df.head(100)))
    assert(len(df1.before) == len(df2.before))
    assert(len(df1.after) == len(df2.after))
    assert df1[df1.before != df2.before].empty
    assert df1[df1.after != df2.after].empty
    

test()

На всякий случай смотрим глазами:

In [38]:
group_by_sentence(train_df.head(1000))

before  \
sentence_id                                                      
0                                   По состоянию на 1862 год .   
1            Оснащались латными рукавицами и сабатонами с н...   
2            В конце 1811 года , вследствие конфликта с про...   
3            Тиберий Юлий Поллиен Ауспекс ( лат . Tiberius ...   
4            Севернее Дудинки и северо - восточнее Белочи ,...   
...                                                        ...   
67           Джон Стюарт , 1-й маркиз Бьют , стал носить эт...   
68           На Плоском Мире восьмисторонняя призма способн...   
69           В 2011 вышел четвертый альбом , Je suis , в 20...   
70           Агатовая Империя занимает почти весь Противове...   
71           Арис представлял себя населению в качестве « м...   

                                                         after  
sentence_id                                                     
0            По состоянию на тысяча восемьсот шестьдесят вт...  
1            Оснащались латными рукавицами и сабатонами с н...  
2            В конце тысяча восемьсот одиннадцатого года , ...  
3            Тиберий Юлий Поллиен Ауспекс ( лат . т_trans и...  
4            Севернее Дудинки и северо - восточнее Белочи ,...  
...                                                        ...  
67           Джон Стюарт , первый маркиз Бьют , стал носить...  
68           На Плоском Мире восьмисторонняя призма способн...  
69           В двух тысячах одиннадцати вышел четвертый аль...  
70           Агатовая Империя занимает почти весь Противове...  
71           Арис представлял себя населению в качестве « м...  

[72 rows x 2 columns]

In [39]:
group_by_sentence(WindowMaker(add_unchanged=True)(train_df.head(1000)))

before  \
sentence_id                                                      
0                                   По состоянию на 1862 год .   
1            Оснащались латными рукавицами и сабатонами с н...   
2            В конце 1811 года , вследствие конфликта с про...   
3            Тиберий Юлий Поллиен Ауспекс ( лат . Tiberius ...   
4            Севернее Дудинки и северо - восточнее Белочи ,...   
...                                                        ...   
67           Джон Стюарт , 1-й маркиз Бьют , стал носить эт...   
68           На Плоском Мире восьмисторонняя призма способн...   
69           В 2011 вышел четвертый альбом , Je suis , в , ...   
70           Агатовая Империя занимает почти весь Противове...   
71           Арис представлял себя населению в качестве « м...   

                                                         after  
sentence_id                                                     
0            По состоянию на тысяча восемьсот шестьдесят вт...  
1            Оснащались латными рукавицами и сабатонами с н...  
2            В конце тысяча восемьсот одиннадцатого года , ...  
3            Тиберий Юлий Поллиен Ауспекс ( лат . т_trans и...  
4            Севернее Дудинки и северо - восточнее Белочи ,...  
...                                                        ...  
67           Джон Стюарт , первый маркиз Бьют , стал носить...  
68           На Плоском Мире восьмисторонняя призма способн...  
69           В двух тысячах одиннадцати вышел четвертый аль...  
70           Агатовая Империя занимает почти весь Противове...  
71           Арис представлял себя населению в качестве « м...  

[72 rows x 2 columns]

Проверяем режим для тестовой выборки, когда after неизвестен

In [40]:
wm = WindowMaker(add_unchanged=True, left_window_size=2, right_window_size=2)
wm(test_df.head(100), mode='test')

before  \
sentence_id                                                        
0           0  Производится в Азии , Африке , России , Турции...   
            1                              с августа 2010 года .   
1           0         Теперь эти замки - туристические объекты .   
2           0           Проверено 26 августа 2012 . Архивировано   
            1       из первоисточника 19 октября 2012 . Интервью   
            2                                      Тараса Хтея .   
3           0                                       — С. 52 . С.   
            1  Карапетян Памятники армянской культуры в зоне ...   
4           0                           В 1902 году было открыто   
            1              только пешеходное движение по мосту .   
5           0            Проверено 1 августа 2013 . Архивировано   
            1             из первоисточника 1 августа 2013 . Ice   
            2                                   . Ice Age : Dawn   
            3   : Dawn of the Dinosaurs for PlayStation 2 ( 2009   
            4                                     ) ( англ . ) .   
6           0                        В качестве ГЭУ корабля была   
            1                                  выбрана дизельная   

                                                           after  different  
sentence_id                                                                  
0           0  Производится в Азии , Африке , России , Турции...      False  
            1                              с августа 2010 года .       True  
1           0         Теперь эти замки - туристические объекты .      False  
2           0           Проверено 26 августа 2012 . Архивировано       True  
            1       из первоисточника 19 октября 2012 . Интервью       True  
            2                                      Тараса Хтея .      False  
3           0                                       — С. 52 . С.       True  
            1  Карапетян Памятники армянской культуры в зоне ...      False  
4           0                           В 1902 году было открыто       True  
            1              только пешеходное движение по мосту .      False  
5           0            Проверено 1 августа 2013 . Архивировано       True  
            1             из первоисточника 1 августа 2013 . Ice       True  
            2                                   . Ice Age : Dawn       True  
            3   : Dawn of the Dinosaurs for PlayStation 2 ( 2009       True  
            4                                     ) ( англ . ) .      False  
6           0                        В качестве ГЭУ корабля была       True  
            1                                  выбрана дизельная      False

In [ ]:
%%time

wm = WindowMaker(add_unchanged=True, left_window_size=2, right_window_size=2)

train_df_windows = wm(_X_train_words)
dev_df_windows = wm(_X_dev_words)


In [ ]:
%%time

wm = WindowMaker(left_window_size=2, right_window_size=2)

train_df_windows = wm(_X_train_words)
dev_df_windows = wm(_X_dev_words)


### Подход 3 -- Char токенизация слов

В этом подходе в качестве Instance у нас просто слово, а в качестве токенов -- его символы

Этот подход не очень правильный, ведь в русском языке форма слова зависит от падежа -- то есть от контекста слова в предложении.
Однако примеров с одинаковым числом, но разными падежами в датасете достаточно мало, при этом встречаются и примеры, которые с точки русского языка -- бред. 
Например, предложение номер 69:

In [32]:
_g = group_by_sentence(WindowMaker(add_unchanged=True)(train_df.head(1000)))
_g[69:70]

before  \
sentence_id                                                      
69           В 2011 вышел четвертый альбом , Je suis , в , ...   

                                                         after  
sentence_id                                                     
69           В двух тысячах одиннадцати вышел четвертый аль...

**В двух тысячах одиннадцати** получен явно каким-то неверным способом. Поэтому, есть надежда, что наш <<халтурный>> способ тоже сработает

Сплитим датасет на слова, но таким образом, чтобы слова из одного предложения были в одной выборке

In [77]:
def _train_test_split(df: pd.DataFrame, idx_column : str, params):
    indices = np.array(list(set(df[idx_column].to_list())))
    train_indices, dev_indices = train_test_split(indices, **params)
    flt = df[idx_column].isin(train_indices)
    return df[flt], df[~flt]

Посмотрим 20 наидлиннейших слов в таргете

In [37]:
sorted(_X_train_words.after.apply(len))[-20:]

[379,
 379,
 388,
 390,
 395,
 395,
 395,
 406,
 417,
 425,
 459,
 486,
 493,
 509,
 574,
 589,
 661,
 677,
 715,
 1003]

Удалим слишком длинные таргеты

In [72]:
train_df_cut = train_df.copy()
train_df_cut = train_df_cut[train_df_cut['before'].apply(len) < 400]
train_df_cut = train_df_cut[train_df_cut['after'].apply(len) < 400]

In [78]:
_X_train_words, _X_dev_words = _train_test_split(
    train_df_cut, 
    idx_column='sentence_id',
    params=dict(test_size=0.1, random_state=3)
)
_X_pretrain_words = _X_train_words.copy()
_X_pretrain_words.after = _X_pretrain_words.before

In [110]:
len(_X_dev_words) / len(_X_train_words)

0.11131697866811584

In [111]:
_X_pretrain_words.to_csv('X_pretrain_words_allennlp.tsv', sep='\t', header=False, columns=['before', 'after'], index=False)
_X_train_words.to_csv('X_train_words_allennlp.tsv', sep='\t', header=False, columns=['before', 'after'], index=False)
_X_dev_words.to_csv('X_dev_words_allennlp.tsv', sep='\t', header=False, columns=['before', 'after'], index=False)
test_df.to_csv('X_test_words_allennlp.tsv', sep='\t', header=False, columns=['before'], index=False)

In [7]:
source_tokenizer = WordTokenizer(
    word_splitter=CharacterWithTransWordSplitter(lowercase_characters=False), 
    end_tokens=['<eos>'],
)
target_tokenizer = WordTokenizer(
    word_splitter=CharacterWithTransWordSplitter(lowercase_characters=False),
    start_tokens=['<sos>'],
)
source_token_indexer =  {
    'tokens': SingleIdTokenIndexer(namespace='tokens')
}
target_token_indexer =  {
    'tokens': SingleIdTokenIndexer(namespace='target_tokens')
}
reader = Seq2SeqDatasetReader(
    source_tokenizer=source_tokenizer,
    target_tokenizer=target_tokenizer,
        source_token_indexers=source_token_indexer,
        target_token_indexers=target_token_indexer,
#         lazy=True
)
# X_dev = reader.read('X_dev_words_allennlp_10000.tsv')
# X_train = reader.read('X_train_words_allennlp_10000.tsv')
# X_pretrain = reader.read('X_pretrain_words_allennlp_10000.tsv')

X_train = reader.read('X_train_words_allennlp.tsv')
X_dev = reader.read('X_dev_words_allennlp.tsv')
X_pretrain = reader.read('X_pretrain_words_allennlp.tsv')

9515287it [08:10, 19396.79it/s]
1059213it [01:18, 13491.34it/s]
9515287it [07:57, 19947.65it/s]


In [ ]:
print(X_train[0])

In [8]:
vocab = Vocabulary.from_instances(X_train + X_pretrain + X_dev,
                                  min_count={'source_tokens': 1,
                                             'target_tokens': 1})

100%|██████████| 20089787/20089787 [03:10<00:00, 105262.71it/s]


In [8]:
vocab.print_statistics()



----Vocabulary Statistics----


Top 10 most frequent tokens in namespace 'tokens':
	Token: @start@		Frequency: 20089787
	Token: <eos>		Frequency: 20089787
	Token: @end@		Frequency: 20089787
	Token: о		Frequency: 8793627
	Token: а		Frequency: 6988017
	Token: е		Frequency: 6929056
	Token: и		Frequency: 6602483
	Token: н		Frequency: 5561417
	Token: р		Frequency: 4750800
	Token: с		Frequency: 4562374

Top 10 longest tokens in namespace 'tokens':
	Token: Heliand.comHelitrans		length: 20	Frequency: 2
	Token: Simutrans		length: 9	Frequency: 4
	Token: @start@		length: 7	Frequency: 20089787
	Token: latrans		length: 7	Frequency: 2
	Token: Intrans		length: 7	Frequency: 2
	Token: Motrans		length: 7	Frequency: 2
	Token: <eos>		length: 5	Frequency: 20089787
	Token: @end@		length: 5	Frequency: 20089787
	Token: trans		length: 5	Frequency: 25
	Token: о		length: 1	Frequency: 8793627

Top 10 shortest tokens in namespace 'tokens':
	Token: 외		length: 1	Frequency: 1
	Token: 休		length: 1	Frequency: 1
	Toke

In [115]:
VOCAB_DIR = "vocabulary2"

In [116]:

vocab.save_to_files(VOCAB_DIR)

In [49]:
vocab = Vocabulary.from_files(VOCAB_DIR)

In [50]:
vocab.get_vocab_size('tokens')

182

In [16]:
CUDA_DEVICE = 0
CUDA_DEVICES = [0, 1]
EN_EMBEDDING_DIM = 256
HIDDEN_DIM = 256
TG_EMBEDDING_DIM = 256

In [508]:


# try:
#     del model
# except:
#     pass

try:
    del trainer
except:
    pass
try:
    del pretrainer
except:
    pass
    

torch.cuda.empty_cache()

In [11]:
# Скалярное произведение -- allennlp.modules.attention.dot_product_attention.DotProductAttention
# Аддитивное внимание -- allennlp.modules.attention.additive_attention.AdditiveAttention
# Мультипликативное внимание -- allennlp.modules.attention.bilinear_attention.BilinearAttention

def get_attentions(hidden_dim, activation = None):
    attentions = {
        'dotproduct' : DotProductAttention(),
        'additive' : AdditiveAttention(hidden_dim, hidden_dim),
        'bilinear' : BilinearAttention(hidden_dim, hidden_dim, activation=activation),
    }
    return attentions

def get_attention(name: str, hidden_dim: int, activation = None):
    return get_attentions(hidden_dim, activation)[name]

In [12]:
def get_encoder(
    name: str,
    encoder_embedding_dim,
    hidden_dim,
    projection_dim=128,
    feedforward_hidden_dim=128,
    num_layers=1,
    num_attention_heads=8,
):
    if name == 'lstm':
        lstm = torch.nn.LSTM(encoder_embedding_dim, hidden_dim, batch_first=True)
        lstm.flatten_parameters()
        return PytorchSeq2SeqWrapper(
            lstm
        )
    if name == 'transformer':
        return  StackedSelfAttentionEncoder(
            input_dim=hidden_dim,
            hidden_dim=hidden_dim,
            projection_dim=projection_dim,
            feedforward_hidden_dim=feedforward_hidden_dim,
            num_layers=num_layers, 
            num_attention_heads=num_attention_heads
        )
    assert False

In [10]:
def get_model(
    *,
    vocab, encoder_params, attention_params,
    max_decoding_steps,
    encoder_embedding_dim,
    target_embedding_dim,
    hidden_dim,
):
    en_embedding = Embedding(num_embeddings=vocab.get_vocab_size('tokens'),
                             embedding_dim=encoder_embedding_dim)
    encoder = get_encoder(encoder_embedding_dim=encoder_embedding_dim, hidden_dim=hidden_dim, **encoder_params)
#     encoder = PytorchSeq2SeqWrapper(
#         torch.nn.LSTM(EN_EMBEDDING_DIM, HIDDEN_DIM, batch_first=True))
#     encoder = StackedSelfAttentionEncoder(input_dim=EN_EMBEDDING_DIM, hidden_dim=HIDDEN_DIM, projection_dim=128, feedforward_hidden_dim=128, num_layers=1, num_attention_heads=8)

    source_embedder = BasicTextFieldEmbedder({"tokens": en_embedding})

    # attention = LinearAttention(HIDDEN_DIM, HIDDEN_DIM, activation=Activation.by_name('tanh')())
    # attention = BilinearAttention(HIDDEN_DIM, HIDDEN_DIM)
#     attention = DotProductAttention()
    attention = get_attention(**attention_params, hidden_dim=hidden_dim)

    model = SimpleSeq2Seq(vocab, source_embedder, encoder, max_decoding_steps,
                          target_embedding_dim=target_embedding_dim,
                          target_namespace='target_tokens',
                          attention=attention,
                          beam_size=8,
                          use_bleu=True)
    model.cuda(CUDA_DEVICE)
    
    return model


def get_trainer(*, model, X_train, X_test, num_epochs=10, patience=None, batch_size=512):
   
    optimizer = optim.Adam(model.parameters())
    iterator = BucketIterator(
        batch_size=batch_size,
        sorting_keys=[("source_tokens", "num_tokens")],
        max_instances_in_memory=batch_size*2,
    )

    iterator.index_with(vocab)

    trainer = Trainer(model=model,
                      optimizer=optimizer,
                      iterator=iterator,
                      train_dataset=X_train,
                      validation_dataset=X_test,
                      patience=patience,
                      num_epochs=num_epochs,
                      cuda_device=CUDA_DEVICES)

    return trainer

def run_trainer(*, model,  trainer, epochs, X_test, print_predictions=True):
    for i in range(epochs):
        print(f'Epoch: {i * trainer._num_epochs}..{(i + 1) * trainer._num_epochs}')
        trainer.train()

        predictor = SimpleSeq2SeqPredictor(model, reader)

        for instance in itertools.islice(X_test, 20):
            if print_predictions:
                print('SOURCE:', ''.join(map(str, instance.fields['source_tokens'].tokens)))
                print('GOLD:', ''.join(map(str, instance.fields['target_tokens'].tokens)))
                print('PRED:', ''.join(map(str, predictor.predict_instance(instance)['predicted_tokens'])))
        print()

In [17]:
model = get_model(
    vocab=vocab,
    encoder_params=dict(
        name='transformer',
        projection_dim=128,
        feedforward_hidden_dim=128,
        num_layers=1,
        num_attention_heads=8,
    ),
    attention_params=dict(
        name='bilinear',
    ),
    max_decoding_steps=400,
    encoder_embedding_dim=EN_EMBEDDING_DIM,
    target_embedding_dim=TG_EMBEDDING_DIM,
    hidden_dim=HIDDEN_DIM,
    
)

In [18]:
pretrainer = get_trainer(model=model, X_train=X_pretrain[:10**6], X_test=X_pretrain[10**6:10**6+100], num_epochs=3)
run_trainer(model=model, trainer=pretrainer, epochs=5, X_test=X_dev)

You provided a validation dataset but patience was set to None, meaning that early stopping is disabled


Epoch: 0..3


loss: 1.0010 ||: 100%|██████████| 977/977 [02:17<00:00,  7.08it/s]
BLEU: 0.9869, loss: 0.0213 ||: 100%|██████████| 1/1 [00:00<00:00,  3.80it/s]
loss: 0.0208 ||: 100%|██████████| 977/977 [01:55<00:00,  8.48it/s]
BLEU: 1.0000, loss: 0.0034 ||: 100%|██████████| 1/1 [00:00<00:00,  3.49it/s]
loss: 0.0091 ||: 100%|██████████| 977/977 [01:55<00:00,  8.45it/s]
BLEU: 1.0000, loss: 0.0008 ||: 100%|██████████| 1/1 [00:00<00:00,  3.60it/s]


SOURCE: @start@По<eos>@end@
GOLD: @start@<sos>По@end@
PRED: <sos>По
SOURCE: @start@состоянию<eos>@end@
GOLD: @start@<sos>состоянию@end@
PRED: <sos>состоянию
SOURCE: @start@на<eos>@end@
GOLD: @start@<sos>на@end@
PRED: <sos>на
SOURCE: @start@1862 год<eos>@end@
GOLD: @start@<sos>тысяча восемьсот шестьдесят второй год@end@
PRED: <sos>1862 год
SOURCE: @start@.<eos>@end@
GOLD: @start@<sos>.@end@
PRED: <sos>.
SOURCE: @start@Севернее<eos>@end@
GOLD: @start@<sos>Севернее@end@
PRED: <sos>Севернее
SOURCE: @start@Дудинки<eos>@end@
GOLD: @start@<sos>Дудинки@end@
PRED: <sos>Дудинки
SOURCE: @start@и<eos>@end@
GOLD: @start@<sos>и@end@
PRED: <sos>и
SOURCE: @start@северо<eos>@end@
GOLD: @start@<sos>северо@end@
PRED: <sos>северо
SOURCE: @start@-<eos>@end@
GOLD: @start@<sos>-@end@
PRED: <sos>-
SOURCE: @start@восточнее<eos>@end@
GOLD: @start@<sos>восточнее@end@
PRED: <sos>восточнее
SOURCE: @start@Белочи<eos>@end@
GOLD: @start@<sos>Белочи@end@
PRED: <sos>Белочи
SOURCE: @start@,<eos>@end@
GOLD: @start@<sos>,

loss: 0.0060 ||: 100%|██████████| 977/977 [01:56<00:00,  8.40it/s]
BLEU: 0.9513, loss: 0.0004 ||: 100%|██████████| 1/1 [00:00<00:00,  3.47it/s]
loss: 0.0055 ||: 100%|██████████| 977/977 [01:55<00:00,  8.47it/s]
BLEU: 1.0000, loss: 0.0006 ||: 100%|██████████| 1/1 [00:00<00:00,  3.48it/s]
loss: 0.0046 ||: 100%|██████████| 977/977 [01:55<00:00,  8.48it/s]
BLEU: 1.0000, loss: 0.0002 ||: 100%|██████████| 1/1 [00:00<00:00,  3.81it/s]


...

SOURCE: @start@По<eos>@end@
GOLD: @start@<sos>По@end@
PRED: <sos>По
SOURCE: @start@состоянию<eos>@end@
GOLD: @start@<sos>состоянию@end@
PRED: <sos>состоянию
SOURCE: @start@на<eos>@end@
GOLD: @start@<sos>на@end@
PRED: <sos>на
SOURCE: @start@1862 год<eos>@end@
GOLD: @start@<sos>тысяча восемьсот шестьдесят второй год@end@
PRED: <sos>1862 год
SOURCE: @start@.<eos>@end@
GOLD: @start@<sos>.@end@
PRED: <sos>.
SOURCE: @start@Севернее<eos>@end@
GOLD: @start@<sos>Севернее@end@
PRED: <sos>Севернее
SOURCE: @start@Дудинки<eos>@end@
GOLD: @start@<sos>Дудинки@end@
PRED: <sos>Дудинки
SOURCE: @start@и<eos>@end@
GOLD: @start@<sos>и@end@
PRED: <sos>и
SOURCE: @start@северо<eos>@end@
GOLD: @start@<sos>северо@end@
PRED: <sos>северо
SOURCE: @start@-<eos>@end@
GOLD: @start@<sos>-@end@
PRED: <sos>-
SOURCE: @start@восточнее<eos>@end@
GOLD: @start@<sos>восточнее@end@
PRED: <sos>восточнее
SOURCE: @start@Белочи<eos>@end@
GOLD: @start@<sos>Белочи@end@
PRED: <sos>Белочи
SOURCE: @start@,<eos>@end@
GOLD: @start@<sos>,

loss: 0.0023 ||: 100%|██████████| 977/977 [01:55<00:00,  8.46it/s]
BLEU: 0.9513, loss: 0.0000 ||: 100%|██████████| 1/1 [00:00<00:00,  2.49it/s]
loss: 0.0016 ||: 100%|██████████| 977/977 [01:55<00:00,  8.46it/s]
BLEU: 1.0000, loss: 0.0000 ||: 100%|██████████| 1/1 [00:00<00:00,  3.33it/s]
loss: 0.0015 ||: 100%|██████████| 977/977 [01:55<00:00,  8.45it/s]
BLEU: 1.0000, loss: 0.0000 ||: 100%|██████████| 1/1 [00:00<00:00,  3.53it/s]


SOURCE: @start@По<eos>@end@
GOLD: @start@<sos>По@end@
PRED: <sos>По
SOURCE: @start@состоянию<eos>@end@
GOLD: @start@<sos>состоянию@end@
PRED: <sos>состоянию
SOURCE: @start@на<eos>@end@
GOLD: @start@<sos>на@end@
PRED: <sos>на
SOURCE: @start@1862 год<eos>@end@
GOLD: @start@<sos>тысяча восемьсот шестьдесят второй год@end@
PRED: <sos>1862 год
SOURCE: @start@.<eos>@end@
GOLD: @start@<sos>.@end@
PRED: <sos>.
SOURCE: @start@Севернее<eos>@end@
GOLD: @start@<sos>Севернее@end@
PRED: <sos>Севернее
SOURCE: @start@Дудинки<eos>@end@
GOLD: @start@<sos>Дудинки@end@
PRED: <sos>Дудинки
SOURCE: @start@и<eos>@end@
GOLD: @start@<sos>и@end@
PRED: <sos>и
SOURCE: @start@северо<eos>@end@
GOLD: @start@<sos>северо@end@
PRED: <sos>северо
SOURCE: @start@-<eos>@end@
GOLD: @start@<sos>-@end@
PRED: <sos>-
SOURCE: @start@восточнее<eos>@end@
GOLD: @start@<sos>восточнее@end@
PRED: <sos>восточнее
SOURCE: @start@Белочи<eos>@end@
GOLD: @start@<sos>Белочи@end@
PRED: <sos>Белочи
SOURCE: @start@,<eos>@end@
GOLD: @start@<sos>,

loss: 0.0028 ||: 100%|██████████| 977/977 [01:55<00:00,  8.45it/s]
BLEU: 0.9417, loss: 0.0027 ||: 100%|██████████| 1/1 [00:00<00:00,  3.72it/s]
loss: 0.0043 ||: 100%|██████████| 977/977 [01:55<00:00,  8.43it/s]
BLEU: 1.0000, loss: 0.0002 ||: 100%|██████████| 1/1 [00:00<00:00,  3.72it/s]
loss: 0.0015 ||: 100%|██████████| 977/977 [01:56<00:00,  8.42it/s]
BLEU: 1.0000, loss: 0.0000 ||: 100%|██████████| 1/1 [00:00<00:00,  3.09it/s]


SOURCE: @start@По<eos>@end@
GOLD: @start@<sos>По@end@
PRED: <sos>По
SOURCE: @start@состоянию<eos>@end@
GOLD: @start@<sos>состоянию@end@
PRED: <sos>состоянию
SOURCE: @start@на<eos>@end@
GOLD: @start@<sos>на@end@
PRED: <sos>на
SOURCE: @start@1862 год<eos>@end@
GOLD: @start@<sos>тысяча восемьсот шестьдесят второй год@end@
PRED: <sos>1862 год
SOURCE: @start@.<eos>@end@
GOLD: @start@<sos>.@end@
PRED: <sos>.
SOURCE: @start@Севернее<eos>@end@
GOLD: @start@<sos>Севернее@end@
PRED: <sos>Севернее
SOURCE: @start@Дудинки<eos>@end@
GOLD: @start@<sos>Дудинки@end@
PRED: <sos>Дудинки
SOURCE: @start@и<eos>@end@
GOLD: @start@<sos>и@end@
PRED: <sos>и
SOURCE: @start@северо<eos>@end@
GOLD: @start@<sos>северо@end@
PRED: <sos>северо
SOURCE: @start@-<eos>@end@
GOLD: @start@<sos>-@end@
PRED: <sos>-
SOURCE: @start@восточнее<eos>@end@
GOLD: @start@<sos>восточнее@end@
PRED: <sos>восточнее
SOURCE: @start@Белочи<eos>@end@
GOLD: @start@<sos>Белочи@end@
PRED: <sos>Белочи
SOURCE: @start@,<eos>@end@
GOLD: @start@<sos>,

In [138]:
with open(f"./models/transformers_dotproduct_default1.th", 'wb') as f:
    torch.save(model.state_dict(), f)

In [19]:
del pretrainer
torch.cuda.empty_cachety_cache()

In [44]:
trainer = get_trainer(model=model, X_train=X_train[:10**6], X_test=X_dev[:10000], num_epochs=3, patience=2)
run_trainer(model=model, trainer=trainer, epochs=10, X_test=X_dev[:10000])

Epoch: 0..3


loss: 0.0079 ||: 100%|██████████| 977/977 [03:47<00:00,  4.29it/s]
BLEU: 0.9312, loss: 0.2639 ||: 100%|██████████| 10/10 [01:36<00:00,  9.66s/it]
loss: 0.0076 ||: 100%|██████████| 977/977 [03:45<00:00,  4.33it/s]
BLEU: 0.9702, loss: 0.2833 ||: 100%|██████████| 10/10 [01:25<00:00,  8.54s/it]
loss: 0.0074 ||: 100%|██████████| 977/977 [03:48<00:00,  4.28it/s]
BLEU: 0.9714, loss: 0.2631 ||: 100%|██████████| 10/10 [01:33<00:00,  9.40s/it]


SOURCE: По<eos>
GOLD: <sos>По
PRED: <sos>По
SOURCE: состоянию<eos>
GOLD: <sos>состоянию
PRED: <sos>состоянию
SOURCE: на<eos>
GOLD: <sos>на
PRED: <sos>на
SOURCE: 1862 год<eos>
GOLD: <sos>тысяча восемьсот шестьдесят второй год
PRED: <sos>тысяча восемьсот шестьдесят второй год
SOURCE: .<eos>
GOLD: <sos>.
PRED: <sos>.
SOURCE: Севернее<eos>
GOLD: <sos>Севернее
PRED: <sos>Севернее
SOURCE: Дудинки<eos>
GOLD: <sos>Дудинки
PRED: <sos>Дудинки
SOURCE: и<eos>
GOLD: <sos>и
PRED: <sos>и
SOURCE: северо<eos>
GOLD: <sos>северо
PRED: <sos>северо
SOURCE: -<eos>
GOLD: <sos>-
PRED: <sos>-
SOURCE: восточнее<eos>
GOLD: <sos>восточнее
PRED: <sos>восточнее
SOURCE: Белочи<eos>
GOLD: <sos>Белочи
PRED: <sos>Белочи
SOURCE: ,<eos>
GOLD: <sos>,
PRED: <sos>,
SOURCE: в<eos>
GOLD: <sos>в
PRED: <sos>в
SOURCE: низменной<eos>
GOLD: <sos>низменной
PRED: <sos>низменной
SOURCE: долине<eos>
GOLD: <sos>долине
PRED: <sos>долине
SOURCE: Неруссы<eos>
GOLD: <sos>Неруссы
PRED: <sos>Неруссы
SOURCE: —<eos>
GOLD: <sos>—
PRED: <sos>—
S

loss: 0.0072 ||: 100%|██████████| 977/977 [03:36<00:00,  4.51it/s]
BLEU: 0.9727, loss: 0.2827 ||: 100%|██████████| 10/10 [01:24<00:00,  8.48s/it]
loss: 0.0069 ||: 100%|██████████| 977/977 [03:37<00:00,  4.49it/s]
BLEU: 0.9726, loss: 0.2727 ||: 100%|██████████| 10/10 [01:25<00:00,  8.59s/it]


SOURCE: По<eos>
GOLD: <sos>По
PRED: <sos>По
SOURCE: состоянию<eos>
GOLD: <sos>состоянию
PRED: <sos>состоянию
SOURCE: на<eos>
GOLD: <sos>на
PRED: <sos>на
SOURCE: 1862 год<eos>
GOLD: <sos>тысяча восемьсот шестьдесят второй год
PRED: <sos>тысяча восемьсот шестьдесят второй год
SOURCE: .<eos>
GOLD: <sos>.
PRED: <sos>.
SOURCE: Севернее<eos>
GOLD: <sos>Севернее
PRED: <sos>Севернее
SOURCE: Дудинки<eos>
GOLD: <sos>Дудинки
PRED: <sos>Дудинки
SOURCE: и<eos>
GOLD: <sos>и
PRED: <sos>и
SOURCE: северо<eos>
GOLD: <sos>северо
PRED: <sos>северо
SOURCE: -<eos>
GOLD: <sos>-
PRED: <sos>-
SOURCE: восточнее<eos>
GOLD: <sos>восточнее
PRED: <sos>восточнее
SOURCE: Белочи<eos>
GOLD: <sos>Белочи
PRED: <sos>Белочи
SOURCE: ,<eos>
GOLD: <sos>,
PRED: <sos>,
SOURCE: в<eos>
GOLD: <sos>в
PRED: <sos>в
SOURCE: низменной<eos>
GOLD: <sos>низменной
PRED: <sos>низменной
SOURCE: долине<eos>
GOLD: <sos>долине
PRED: <sos>долине
SOURCE: Неруссы<eos>
GOLD: <sos>Неруссы
PRED: <sos>Неруссы
SOURCE: —<eos>
GOLD: <sos>—
PRED: <sos>—
S

...

SOURCE: По<eos>
GOLD: <sos>По
PRED: <sos>По
SOURCE: состоянию<eos>
GOLD: <sos>состоянию
PRED: <sos>состоянию
SOURCE: на<eos>
GOLD: <sos>на
PRED: <sos>на
SOURCE: 1862 год<eos>
GOLD: <sos>тысяча восемьсот шестьдесят второй год
PRED: <sos>тысяча восемьсот шестьдесят второй год
SOURCE: .<eos>
GOLD: <sos>.
PRED: <sos>.
SOURCE: Севернее<eos>
GOLD: <sos>Севернее
PRED: <sos>Севернее
SOURCE: Дудинки<eos>
GOLD: <sos>Дудинки
PRED: <sos>Дудинки
SOURCE: и<eos>
GOLD: <sos>и
PRED: <sos>и
SOURCE: северо<eos>
GOLD: <sos>северо
PRED: <sos>северо
SOURCE: -<eos>
GOLD: <sos>-
PRED: <sos>-
SOURCE: восточнее<eos>
GOLD: <sos>восточнее
PRED: <sos>восточнее
SOURCE: Белочи<eos>
GOLD: <sos>Белочи
PRED: <sos>Белочи
SOURCE: ,<eos>
GOLD: <sos>,
PRED: <sos>,
SOURCE: в<eos>
GOLD: <sos>в
PRED: <sos>в
SOURCE: низменной<eos>
GOLD: <sos>низменной
PRED: <sos>низменной
SOURCE: долине<eos>
GOLD: <sos>долине
PRED: <sos>долине
SOURCE: Неруссы<eos>
GOLD: <sos>Неруссы
PRED: <sos>Неруссы
SOURCE: —<eos>
GOLD: <sos>—
PRED: <sos>—
S

loss: 0.0064 ||: 100%|██████████| 977/977 [03:47<00:00,  4.30it/s]
BLEU: 0.9704, loss: 0.2837 ||: 100%|██████████| 10/10 [01:30<00:00,  9.03s/it]


SOURCE: По<eos>
GOLD: <sos>По
PRED: <sos>По
SOURCE: состоянию<eos>
GOLD: <sos>состоянию
PRED: <sos>состоянию
SOURCE: на<eos>
GOLD: <sos>на
PRED: <sos>на
SOURCE: 1862 год<eos>
GOLD: <sos>тысяча восемьсот шестьдесят второй год
PRED: <sos>тысяча восемьсот шестьдесят второй год
SOURCE: .<eos>
GOLD: <sos>.
PRED: <sos>.
SOURCE: Севернее<eos>
GOLD: <sos>Севернее
PRED: <sos>Севернее
SOURCE: Дудинки<eos>
GOLD: <sos>Дудинки
PRED: <sos>Дудинки
SOURCE: и<eos>
GOLD: <sos>и
PRED: <sos>и
SOURCE: северо<eos>
GOLD: <sos>северо
PRED: <sos>северо
SOURCE: -<eos>
GOLD: <sos>-
PRED: <sos>-
SOURCE: восточнее<eos>
GOLD: <sos>восточнее
PRED: <sos>восточнее
SOURCE: Белочи<eos>
GOLD: <sos>Белочи
PRED: <sos>Белочи
SOURCE: ,<eos>
GOLD: <sos>,
PRED: <sos>,
SOURCE: в<eos>
GOLD: <sos>в
PRED: <sos>в
SOURCE: низменной<eos>
GOLD: <sos>низменной
PRED: <sos>низменной
SOURCE: долине<eos>
GOLD: <sos>долине
PRED: <sos>долине
SOURCE: Неруссы<eos>
GOLD: <sos>Неруссы
PRED: <sos>Неруссы
SOURCE: —<eos>
GOLD: <sos>—
PRED: <sos>—
S

loss: 0.0067 ||: 100%|██████████| 977/977 [03:43<00:00,  4.36it/s]
BLEU: 0.9736, loss: 0.2768 ||: 100%|██████████| 10/10 [01:25<00:00,  8.50s/it]


SOURCE: По<eos>
GOLD: <sos>По
PRED: <sos>По
SOURCE: состоянию<eos>
GOLD: <sos>состоянию
PRED: <sos>состоянию
SOURCE: на<eos>
GOLD: <sos>на
PRED: <sos>на
SOURCE: 1862 год<eos>
GOLD: <sos>тысяча восемьсот шестьдесят второй год
PRED: <sos>тысяча восемьсот шестьдесят второй год
SOURCE: .<eos>
GOLD: <sos>.
PRED: <sos>.
SOURCE: Севернее<eos>
GOLD: <sos>Севернее
PRED: <sos>Севернее
SOURCE: Дудинки<eos>
GOLD: <sos>Дудинки
PRED: <sos>Дудинки
SOURCE: и<eos>
GOLD: <sos>и
PRED: <sos>и
SOURCE: северо<eos>
GOLD: <sos>северо
PRED: <sos>северо
SOURCE: -<eos>
GOLD: <sos>-
PRED: <sos>-
SOURCE: восточнее<eos>
GOLD: <sos>восточнее
PRED: <sos>восточнее
SOURCE: Белочи<eos>
GOLD: <sos>Белочи
PRED: <sos>Белочи
SOURCE: ,<eos>
GOLD: <sos>,
PRED: <sos>,
SOURCE: в<eos>
GOLD: <sos>в
PRED: <sos>в
SOURCE: низменной<eos>
GOLD: <sos>низменной
PRED: <sos>низменной
SOURCE: долине<eos>
GOLD: <sos>долине
PRED: <sos>долине
SOURCE: Неруссы<eos>
GOLD: <sos>Неруссы
PRED: <sos>Неруссы
SOURCE: —<eos>
GOLD: <sos>—
PRED: <sos>—
S

In [45]:
with open(f"./models/transformers_dotproduct_default3.th", 'wb') as f:
    torch.save(model.state_dict(), f)

In [46]:
def cut_start_end_tokens(tokens):
    if tokens and tokens[0].text == '@start@':
        tokens.pop(0)
    if tokens and tokens[-1].text == '@end@':
        tokens.pop()
    return tokens

Выведем неугаданные предикты

In [47]:
_predictor = SimpleSeq2SeqPredictor(model, reader)

for instance in itertools.islice(X_dev, 200):
    source = ''.join(map(str, cut_start_end_tokens(instance.fields['source_tokens'].tokens)))
    target = ''.join(map(str, cut_start_end_tokens(instance.fields['target_tokens'].tokens)))
    predicted = ''.join(map(str, _predictor.predict_instance(instance)['predicted_tokens']))
    if target != predicted:
        print('SOURCE:', source)
        print('GOLD:', target)
        print('PRED:', predicted)
        print()
print()

SOURCE: оцентр<eos>
GOLD: <sos>о ц е н т р
PRED: <sos>оцентр

SOURCE: 9 марта<eos>
GOLD: <sos>девятое марта
PRED: <sos>девятого марта

SOURCE: Гаскойн<eos>
GOLD: <sos>Гаскойн
PRED: <sos>мскойн

SOURCE: провел<eos>
GOLD: <sos>провел
PRED: <sos>повел

SOURCE: допрос<eos>
GOLD: <sos>допрос
PRED: <sos>ппрос

SOURCE: Сюзанны<eos>
GOLD: <sos>Сюзанны
PRED: <sos>Сзанны

SOURCE: Уэллс<eos>
GOLD: <sos>Уэллс
PRED: <sos>л л с

SOURCE: Ньюгейте<eos>
GOLD: <sos>Ньюгейте
PRED: <sos>Нюгейте

SOURCE: результате<eos>
GOLD: <sos>результате
PRED: <sos>рзультате

SOURCE: которого<eos>
GOLD: <sos>которого
PRED: <sos>кторого

SOURCE: она<eos>
GOLD: <sos>она
PRED: <sos>оа

SOURCE: подтвердила<eos>
GOLD: <sos>подтвердила
PRED: <sos>пдтвердила

SOURCE: новую<eos>
GOLD: <sos>новую
PRED: <sos>пвую

SOURCE: версию<eos>
GOLD: <sos>версию
PRED: <sos>врсию

SOURCE: Холл<eos>
GOLD: <sos>Холл
PRED: <sos>л л

SOURCE: Прикорневые<eos>
GOLD: <sos>Прикорневые
PRED: <sos>Пикорневые

SOURCE: листья<eos>
GOLD: <sos>листья
PRE

Нативный предикт всего по одному инстансу работает часов 5, поэтому мы написали кода для итерации по батчам

Чуть позже что-то похожее было найдено тут:
https://github.com/allenai/allennlp/blob/master/allennlp/commands/predict.py#L223-L225

Но по факту, из коробки allennlp предиктить по батчам не умеет :(

In [49]:
def convert_row(df : pd.DataFrame):
    data = []
    for i, row in df.iterrows():
        data.append((
            row.before,
            f'{row.sentence_id}_{row.token_id}',
        ))
    new_df = pd.DataFrame(data=data, columns=['before', 'id'])
    return new_df

In [50]:
def convert_row(df : pd.DataFrame):
    ids = df.apply(lambda row: f'{row.sentence_id}_{row.token_id}', axis=1)
    return {
        'id': ids.to_list(),
        'before': df.before.to_list(),
    }

In [51]:
def make_instances(reader, df):
    instances = []
    for i, row in df.iterrows():
        instance = reader.text_to_instance(row.before)
        instances.append(instance)
    return instances

In [52]:
def batch_iterator(iterable, batch_size=1):
    size = len(iterable)
    for ndx in range(0, size, batch_size):
        yield iterable[ndx:min(ndx + batch_size, size)]

In [53]:
def predict_batch(predictor : SimpleSeq2SeqPredictor, rows) -> List[str]:
    
    reader = predictor._dataset_reader
    instances = make_instances(reader, rows)
    
    predictions = predictor.predict_batch_instance(instances)
    
    res = []
    for predicted, before in zip(predictions, rows.before):
        predicted = predicted['predicted_tokens']
        if predicted and predicted[0] == '<sos>':
            predicted.pop(0)
        if predicted and predicted[-1] == '<eos>':
            predicted.pop()
        if len(predicted) == 0:
            predicted = [before]
        predicted = ''.join(predicted)
        res.append(predicted)
    return res

In [54]:
def predict_whole_df(predictor : SimpleSeq2SeqPredictor, df : pd.DataFrame, batch_size : int):
    reader = predictor._dataset_reader  
    
    print('predicting...')
    
    after = []
    before = []
    total = len(df) / batch_size
    ids = []
    for rows_batch in tqdm(batch_iterator(df, batch_size), total=total):
        
        predicted = predict_batch(predictor=predictor, rows=rows_batch)
        after += predicted
        
        current_ids = rows_batch.apply(lambda row: f'{row.sentence_id}_{row.token_id}', axis=1)
        ids += current_ids.to_list()
        
        before += rows_batch.before.to_list()
        
    print('predicted!')
    
    return pd.DataFrame({
        'id': ids,
        'after': after,
        'before': before,
    })
        

In [55]:
def make_predict(*, model, df, batch_size):
    model.eval()
    predictor = SimpleSeq2SeqPredictor(model, reader)
    print('groupping...')
    new_df = predict_whole_df(predictor, df, batch_size)
    return new_df

In [56]:
def predict_and_make_submission(model, df, model_name, batch_size):
    predicted_df = make_predict(model=model, df=df, batch_size=batch_size)
    predicted_df.to_csv(f'predictions/{model_name}.csv', columns=['id', 'after'], index=False, quoting=1)

С предиктом по батчам удалось добиться времени порядка 40 минут -- заметно лучше, чем 5 часов :)

In [479]:
model.eval()

predict_and_make_submission(model, test_df, 'transformers_dotproduct_default', batch_size=1024)

groupping...
predicting...



predicted!


In [503]:
torch.cuda.empty_cache()


Потом оказалось, что сдавать нужно test2, а не test....

In [505]:
predict_and_make_submission(model, test2_df, 'transformers_dotproduct_default2', batch_size=2048)

groupping...
predicting...



predicted!


**Kaggle:**
https://www.kaggle.com/submissions/15591854/15591854.raw

Private Score -- 0.91619

Public Score -- 0.91502


Далее был написан код для перебора параметров по сетке. 
Но он очень долго работает.
Также возникли проблемы с тем, что torch.cuda.empty() не до конца очищал память и подбор параметров падал с ошибкой по памяти

In [21]:
class Seq2SeqParams:
    def __init__(
        self,
        hidden_dim: int = 256,
        encoder_embedding_dim: int = 256,
        target_embedding_dim: int = 256,
        encoder_params=dict(
            name='transformer',
        ),
        attention_params=dict(
            name='dotproduct',
        ),
    ):
        self.hidden_dim = hidden_dim
        self.encoder_embedding_dim = encoder_embedding_dim
        self.target_embedding_dim = target_embedding_dim
        self.encoder_params = encoder_params
        self.attention_params = attention_params
    
    def as_dict(self):
        return dict(
            hidden_dim=self.hidden_dim,
            encoder_embedding_dim=self.encoder_embedding_dim,
            target_embedding_dim=self.target_embedding_dim,
            encoder_params=self.encoder_params,
            attention_params=self.attention_params,
        )

In [522]:
_p = Seq2SeqParams()
_p.get_model_name()

"hidden_dim:256-encoder_embedding_dim:256-target_embedding_dim:256-encoder_params:{'name': 'transformer'}-attention_params:{'name': 'dotproduct'}"

In [118]:
def build_train_eval(
    *, 
    vocab,
    X_pretrain, 
    X_train,
    X_dev,
    X_dev_df,
    params: Seq2SeqParams,
    use_pretrain,
    batch_epochs, 
    training_batches,
    batch_size,
):
    current_model = get_model(
        vocab=vocab,
        max_decoding_steps=400,
        **params.as_dict()
    )
    
    if use_pretrain:
        pretrainer = get_trainer(model=current_model, X_train=X_pretrain, X_test=X_dev, num_epochs=batch_epochs, batch_size=batch_size)
        run_trainer(model=current_model, trainer=pretrainer, epochs=training_batches, X_test=X_dev, print_predictions=False)

        del pretrainer
        torch.cuda.empty_cache()
    
    trainer = get_trainer(model=current_model, X_train=X_train, X_test=X_dev, num_epochs=batch_epochs, batch_size=batch_size)
    run_trainer(model=current_model, trainer=trainer, epochs=training_batches, X_test=X_dev, print_predictions=False)
    
    predicted = make_predict(model=current_model, df=X_dev_df, batch_size=batch_size)
    print(predicted.head())
    bleu = current_model.get_metrics()['BLEU']
    return current_model, bleu


def save_model(model, model_name):
    with open(f"./models/{model_name}.th", 'wb') as f:
        torch.save(model.state_dict(), f)
    

def eval_grid(
    *,
    vocab,
    X_pretrain,
    X_train,
    X_dev,
    X_dev_df : pd.DataFrame,
    test_df: pd.DataFrame,
    batch_epochs,
    training_batches,
    batch_size,
):
#     hidden_dims = [128, 256, 512]
#     encoder_embedding_dims = [128, 256, 512]
#     target_embedding_dims = [128, 256, 512]
    encoder_params_list = [
        dict(name='transformer'),
        dict(name='lstm'),
    ]
    attention_params_list = [
        dict(name='dotproduct'),
        dict(name='additive'),
        dict(name='bilinear'),
    ]
    best_model_name = None
    best_model_params = None
    best_bleu = -1
    hidden_dim = 256
    encoder_embedding_dim = 256
    target_embedding_dim = 256
#     for hidden_dim in hidden_dims:
#         for encoder_emmbeding_dim in encoder_embedding_dims:
#             for target_embedding_dim in target_embedding_dims:
    model_no = 0
    for use_pretrain in [True]:
        for encoder_params in encoder_params_list:
            for attention_params in attention_params_list:
                params = Seq2SeqParams(
                    hidden_dim=hidden_dim,
                    encoder_embedding_dim=encoder_embedding_dim,
                    target_embedding_dim=target_embedding_dim,
                    encoder_params=encoder_params,
                    attention_params=attention_params,
                )
                encoder_name = encoder_params["name"]
                attention_name = attention_params["name"]
                model_name = f'eval_grid_{model_no}_{encoder_name}_{attention_name}'
                print(f'params for "{model_name}" are "{params.as_dict()}"')
                print(f'use_pretrain={use_pretrain}')
                model, bleu = build_train_eval(
                    vocab=vocab,
                    X_pretrain=X_pretrain, 
                    X_train=X_train, 
                    X_dev=X_dev,
                    X_dev_df=X_dev_df,
                    params=params,
                    use_pretrain=use_pretrain,
                    batch_epochs=batch_epochs,
                    training_batches=training_batches,
                    batch_size=batch_size,
                )
                predict_and_make_submission(model=model, df=test_df, model_name=model_name, batch_size=batch_size)
                save_model(model, model_name)
#               del model
    
                torch.cuda.empty_cache()
                model_no += 1
                print()
    
    return best_bleu, best_model_name, best_model_params

In [115]:
eval_grid(
    vocab=vocab,
    X_pretrain=X_pretrain[:10],
    X_train=X_train[:10],
    X_dev=X_dev[:10],
    X_dev_df=_X_dev_words[:10],
    test_df=test2_df[:10],
    batch_epochs=1,
    training_batches=1,
    batch_size=512,
)

You provided a validation dataset but patience was set to None, meaning that early stopping is disabled


params for "eval_grid_0_transformer_dotproduct" are "{'hidden_dim': 256, 'encoder_embedding_dim': 256, 'target_embedding_dim': 256, 'encoder_params': {'name': 'transformer'}, 'attention_params': {'name': 'dotproduct'}}"
use_pretrain=True
Epoch: 0..1


loss: 7.8981 ||: 100%|██████████| 1/1 [00:00<00:00, 26.26it/s]
BLEU: 0.0000, loss: 7.5089 ||: 100%|██████████| 1/1 [00:00<00:00,  1.47it/s]
You provided a validation dataset but patience was set to None, meaning that early stopping is disabled



Epoch: 0..1


loss: 7.4897 ||: 100%|██████████| 1/1 [00:00<00:00, 27.65it/s]
BLEU: 0.0000, loss: 7.0977 ||: 100%|██████████| 1/1 [00:00<00:00, 18.99it/s]

...

loss: 7.8661 ||: 100%|██████████| 1/1 [00:00<00:00, 22.98it/s]
BLEU: 0.0000, loss: 7.8451 ||: 100%|██████████| 1/1 [00:00<00:00, 10.58it/s]


groupping...
predicting...



predicted!
    id after     before
0  0_0    ии         По
1  0_1    ии  состоянию
2  0_2    ии         на
3  0_3    ии   1862 год
4  0_4    ии          .
groupping...
predicting...



predicted!



(-1, None, None)

In [104]:
torch.cuda.empty_cache()

In [119]:
eval_grid(
    vocab=vocab,
    X_pretrain=X_pretrain[:10**6],
    X_train=X_train[:10**6],
    X_dev=X_dev[:10**3],
    X_dev_df=_X_dev_words[:10**3],
    test_df=test2_df,
    batch_epochs=5,
    training_batches=5,
    batch_size=1024,
)

You provided a validation dataset but patience was set to None, meaning that early stopping is disabled


params for "eval_grid_0_transformer_dotproduct" are "{'hidden_dim': 256, 'encoder_embedding_dim': 256, 'target_embedding_dim': 256, 'encoder_params': {'name': 'transformer'}, 'attention_params': {'name': 'dotproduct'}}"
use_pretrain=True
Epoch: 0..5


loss: 1.6266 ||: 100%|██████████| 489/489 [01:55<00:00,  4.23it/s]
BLEU: 0.7008, loss: 1.2140 ||: 100%|██████████| 1/1 [00:03<00:00,  3.97s/it]
loss: 0.0786 ||: 100%|██████████| 489/489 [01:40<00:00,  4.84it/s]
BLEU: 0.7626, loss: 1.3437 ||: 100%|██████████| 1/1 [00:03<00:00,  3.98s/it]
loss: 0.0133 ||: 100%|██████████| 489/489 [01:41<00:00,  4.84it/s]
BLEU: 0.7632, loss: 1.4336 ||: 100%|██████████| 1/1 [00:04<00:00,  4.02s/it]
loss: 0.0071 ||: 100%|██████████| 489/489 [01:42<00:00,  4.78it/s]
BLEU: 0.7626, loss: 1.4816 ||: 100%|██████████| 1/1 [00:03<00:00,  3.94s/it]
loss: 0.0053 ||: 100%|██████████| 489/489 [01:41<00:00,  4.84it/s]
BLEU: 0.7632, loss: 1.5562 ||: 100%|██████████| 1/1 [00:03<00:00,  3.78s/it]



Epoch: 5..10


loss: 0.0085 ||: 100%|██████████| 489/489 [01:42<00:00,  4.76it/s]
BLEU: 0.7632, loss: 1.5200 ||: 100%|██████████| 1/1 [00:03<00:00,  3.91s/it]
loss: 0.0036 ||: 100%|██████████| 489/489 [01:38<00:00,  4.98it/s]
BLEU: 0.7632, loss: 1.6026 ||: 100%|██████████| 1/1 [00:03<00:00,  3.84s/it]
loss: 0.0051 ||: 100%|██████████| 489/489 [02:08<00:00,  3.82it/s]
BLEU: 0.7631, loss: 1.5987 ||: 100%|██████████| 1/1 [00:06<00:00,  6.56s/it]
loss: 0.0033 ||: 100%|██████████| 489/489 [01:40<00:00,  4.86it/s]
BLEU: 0.7632, loss: 1.6194 ||: 100%|██████████| 1/1 [00:03<00:00,  3.85s/it]
loss: 0.0045 ||: 100%|██████████| 489/489 [01:41<00:00,  4.84it/s]
BLEU: 0.7623, loss: 1.6295 ||: 100%|██████████| 1/1 [00:05<00:00,  5.95s/it]


...


Epoch: 20..25


loss: 0.0002 ||: 100%|██████████| 489/489 [02:07<00:00,  3.84it/s]
BLEU: 0.7632, loss: 1.8076 ||: 100%|██████████| 1/1 [00:04<00:00,  4.23s/it]
loss: 0.0002 ||: 100%|██████████| 489/489 [02:07<00:00,  3.84it/s]
BLEU: 0.7632, loss: 1.8098 ||: 100%|██████████| 1/1 [00:04<00:00,  4.49s/it]
loss: 0.0002 ||: 100%|██████████| 489/489 [02:06<00:00,  3.86it/s]
BLEU: 0.7632, loss: 1.8011 ||: 100%|██████████| 1/1 [00:04<00:00,  4.08s/it]
loss: 0.0136 ||: 100%|██████████| 489/489 [02:05<00:00,  3.90it/s]
BLEU: 0.7632, loss: 1.5230 ||: 100%|██████████| 1/1 [00:04<00:00,  4.18s/it]
loss: 0.0006 ||: 100%|██████████| 489/489 [02:03<00:00,  3.96it/s]
BLEU: 0.7632, loss: 1.6182 ||: 100%|██████████| 1/1 [00:04<00:00,  4.34s/it]
You provided a validation dataset but patience was set to None, meaning that early stopping is disabled



Epoch: 0..5


loss: 0.2196 ||:  45%|████▌     | 221/489 [02:02<02:28,  1.81it/s]


RuntimeError: CUDA out of memory. Tried to allocate 1.87 GiB (GPU 0; 31.72 GiB total capacity; 25.81 GiB already allocated; 1.09 GiB free; 3.69 GiB cached)

In [58]:
model = get_model(
    vocab=vocab,
    encoder_params=dict(
        name='lstm',
        projection_dim=128,
        feedforward_hidden_dim=128,
        num_layers=1,
        num_attention_heads=8,
    ),
    attention_params=dict(
        name='bilinear',
    ),
    max_decoding_steps=400,
    encoder_embedding_dim=256,
    target_embedding_dim=256,
    hidden_dim=256,
    
)

In [50]:
pretrainer = get_trainer(model=model, X_train=X_pretrain[:10**6], X_test=X_pretrain[10**6:10**6+100], num_epochs=3)
run_trainer(model=model, trainer=pretrainer, epochs=5, X_test=X_dev)

Epoch: 0..3


  0%|          | 0/377 [00:00<?, ?it/s]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights again call flatten_parameters().
loss: 7.6895 ||:   0%|          | 1/377 [00:07<44:59,  7.18s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights again call flatten_parameters().
loss: 7.6752 ||:   1%|          | 2/377 [00:09<34:57,  5.59s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights again call flatten_parameters

loss: 5.2582 ||:   6%|▋         | 24/377 [00:33<06:05,  1.03s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights again call flatten_parameters().
loss: 5.2001 ||:   7%|▋         | 25/377 [00:34<06:02,  1.03s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights again call flatten_parameters().
loss: 5.1472 ||:   7%|▋         | 26/377 [00:35<06:15,  1.07s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights a

loss: 4.5107 ||:  13%|█▎        | 48/377 [00:59<05:49,  1.06s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights again call flatten_parameters().
loss: 4.4945 ||:  13%|█▎        | 49/377 [01:01<06:02,  1.11s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights again call flatten_parameters().
loss: 4.4784 ||:  13%|█▎        | 50/377 [01:02<06:01,  1.11s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights a

loss: 4.2441 ||:  19%|█▉        | 72/377 [01:28<05:53,  1.16s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights again call flatten_parameters().
loss: 4.2367 ||:  19%|█▉        | 73/377 [01:29<05:39,  1.12s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights again call flatten_parameters().
loss: 4.2294 ||:  20%|█▉        | 74/377 [01:30<06:09,  1.22s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights a

...

loss: 0.0040 ||:  81%|████████  | 304/377 [05:07<01:15,  1.03s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights again call flatten_parameters().
loss: 0.0040 ||:  81%|████████  | 305/377 [05:08<01:12,  1.01s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights again call flatten_parameters().
loss: 0.0040 ||:  81%|████████  | 306/377 [05:09<01:11,  1.00s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weight

loss: 0.0039 ||:  87%|████████▋ | 328/377 [05:34<01:11,  1.46s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights again call flatten_parameters().
loss: 0.0039 ||:  87%|████████▋ | 329/377 [05:35<01:02,  1.30s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights again call flatten_parameters().
loss: 0.0039 ||:  88%|████████▊ | 330/377 [05:36<00:55,  1.18s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weight

loss: 0.0039 ||:  93%|█████████▎| 352/377 [05:59<00:24,  1.03it/s]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights again call flatten_parameters().
loss: 0.0039 ||:  94%|█████████▎| 353/377 [06:00<00:22,  1.05it/s]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights again call flatten_parameters().
loss: 0.0039 ||:  94%|█████████▍| 354/377 [06:00<00:21,  1.06it/s]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weight

loss: 0.0038 ||: 100%|██████████| 377/377 [06:23<00:00,  1.02s/it]
0it [00:00, ?it/s]


SOURCE: @start@По<eos>@end@
GOLD: @start@<sos>По@end@
PRED: <sos>Поналаалаалаалаалаалаалаалаалаалаалаалаалаалаалаалаалаалалаалалаалалаалалаалалаалалаалалаалалаалаюлалаалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалаалалалала
SOURCE: @start@состоянию<eos>@end@
GOLD: @start@<sos>состоянию@end@
PRED: <sos>состояниюналаояниюталаютияниюталаююталаюталаюталаюталаюталаююталаюталаюталаютыяниюталаюяниюталаюяниюталаюяниюталаюяниюталаюяниюталаюяниюталаюяниюталаюяниюталаюяниюталаюяниюталаюяниюталаюяниюталаюяниюталаюяниюталаюяниюталаюяниюталаюяниюталаюяниюталаюяниюталаюяниюталаюяниюталаюяниюталаюяниюталаюяниюталаюяниюталаюяниюталаюяниюталаютьяниюталаютьяниюталатяяниюталатяяниюталатяяниюналаютяяниюталаютяянию
SOURCE: @start@на<eos>@end@
GOLD: @start@<sos>на@end@
PR

In [51]:
trainer = get_trainer(model=model, X_train=X_train[:10**6], X_test=X_dev[:100], num_epochs=3, patience=2)
run_trainer(model=model, trainer=trainer, epochs=10, X_test=X_dev[:100])

Epoch: 0..3


  0%|          | 0/377 [00:00<?, ?it/s]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights again call flatten_parameters().
loss: 5.9888 ||:   0%|          | 1/377 [00:02<18:47,  3.00s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights again call flatten_parameters().
loss: 6.0085 ||:   1%|          | 2/377 [00:05<18:38,  2.98s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights again call flatten_parameters

loss: 6.3738 ||:   6%|▋         | 24/377 [00:56<13:05,  2.22s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights again call flatten_parameters().
loss: 6.2728 ||:   7%|▋         | 25/377 [00:59<13:02,  2.22s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights again call flatten_parameters().
loss: 6.1718 ||:   7%|▋         | 26/377 [01:01<13:12,  2.26s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights a

loss: 4.5844 ||:  13%|█▎        | 48/377 [01:51<11:51,  2.16s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights again call flatten_parameters().
loss: 4.5386 ||:  13%|█▎        | 49/377 [01:53<12:02,  2.20s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights again call flatten_parameters().
loss: 4.4945 ||:  13%|█▎        | 50/377 [01:55<12:05,  2.22s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights a

loss: 3.7763 ||:  19%|█▉        | 72/377 [02:45<11:21,  2.24s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights again call flatten_parameters().
loss: 3.7520 ||:  19%|█▉        | 73/377 [02:47<11:08,  2.20s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights again call flatten_parameters().
loss: 3.7281 ||:  20%|█▉        | 74/377 [02:50<11:32,  2.28s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights a

...

loss: 0.7034 ||:  76%|███████▋  | 288/377 [09:58<03:03,  2.06s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights again call flatten_parameters().
loss: 0.7016 ||:  77%|███████▋  | 289/377 [10:00<02:57,  2.02s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights again call flatten_parameters().
loss: 0.6999 ||:  77%|███████▋  | 290/377 [10:02<02:53,  2.00s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weight

loss: 0.6649 ||:  83%|████████▎ | 312/377 [10:47<02:10,  2.00s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights again call flatten_parameters().
loss: 0.6634 ||:  83%|████████▎ | 313/377 [10:49<02:06,  1.98s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights again call flatten_parameters().
loss: 0.6619 ||:  83%|████████▎ | 314/377 [10:51<02:04,  1.97s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weight

loss: 0.6323 ||:  89%|████████▉ | 336/377 [11:39<01:27,  2.14s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights again call flatten_parameters().
loss: 0.6309 ||:  89%|████████▉ | 337/377 [11:41<01:25,  2.13s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights again call flatten_parameters().
loss: 0.6296 ||:  90%|████████▉ | 338/377 [11:44<01:26,  2.22s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weight

loss: 0.6024 ||:  95%|█████████▌| 360/377 [12:29<00:34,  2.02s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights again call flatten_parameters().
loss: 0.6013 ||:  96%|█████████▌| 361/377 [12:31<00:32,  2.01s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weights again call flatten_parameters().
loss: 0.6001 ||:  96%|█████████▌| 362/377 [12:33<00:30,  2.01s/it]/pytorch/aten/src/ATen/native/cudnn/RNN.cpp:1238: UserWarning: RNN module weights are not part of single contiguous chunk of memory. This means they need to be compacted at every call, possibly greatly increasing memory usage. To compact weight

SOURCE: @start@По<eos>@end@
GOLD: @start@<sos>По@end@
PRED: <sos>Поначассал сол сема ( Поналс ноль нол ( Поналсан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Понан ( Пона
SOURCE: @start@состоянию<eos>@end@
GOLD: @start@<sos>состоянию@end@
PRED: <sos>состоянию » стоянию » стоянию »
SOURCE: @start@на<eos>@end@
GOLD: @start@<sos>на@end@
PRED: <sos>нана » а_trans л_trans т_tran к_trans к_trans к_tran ф_trans т_trans т_trans т_trans т_trans т_trans т_trans т_trans т_trans т_trans т_trans т_trans т_trans т_trans т_trans т_trans т_trans т_trans т_trans т_trans т_trans т_trans т_trans т_trans т_trans т_trans т_trans т_trans т_trans т_trans т_trans т_trans т_trans т_trans т_trans т_trans т_trans т_trans т_

In [61]:
model.eval()

predict_and_make_submission(model, test2_df, 'transformers_dotproduct_default_many_epochs', batch_size=1024)

groupping...
predicting...



predicted!


## Часть 4. [1 балл] Итоги
Напишите краткое резюме проделанной работы. Проведите анализ ошибок: когда модель ошибается? Можно ли скзаать, почему модель ошибается? Сравните результаты всех разработанных моделей. Что помогло вам в выполнении работы, чего не хватало?

**Когда модель ошибается? **
Для наглядности скопируем cell, который был выше:

In [47]:
_predictor = SimpleSeq2SeqPredictor(model, reader)

for instance in itertools.islice(X_dev, 200):
    source = ''.join(map(str, cut_start_end_tokens(instance.fields['source_tokens'].tokens)))
    target = ''.join(map(str, cut_start_end_tokens(instance.fields['target_tokens'].tokens)))
    predicted = ''.join(map(str, _predictor.predict_instance(instance)['predicted_tokens']))
    if target != predicted:
        print('SOURCE:', source)
        print('GOLD:', target)
        print('PRED:', predicted)
        print()
print()

SOURCE: оцентр<eos>
GOLD: <sos>о ц е н т р
PRED: <sos>оцентр

SOURCE: 9 марта<eos>
GOLD: <sos>девятое марта
PRED: <sos>девятого марта

SOURCE: Гаскойн<eos>
GOLD: <sos>Гаскойн
PRED: <sos>мскойн

SOURCE: провел<eos>
GOLD: <sos>провел
PRED: <sos>повел

SOURCE: допрос<eos>
GOLD: <sos>допрос
PRED: <sos>ппрос

SOURCE: Сюзанны<eos>
GOLD: <sos>Сюзанны
PRED: <sos>Сзанны

SOURCE: Уэллс<eos>
GOLD: <sos>Уэллс
PRED: <sos>л л с

SOURCE: Ньюгейте<eos>
GOLD: <sos>Ньюгейте
PRED: <sos>Нюгейте

SOURCE: результате<eos>
GOLD: <sos>результате
PRED: <sos>рзультате

SOURCE: которого<eos>
GOLD: <sos>которого
PRED: <sos>кторого

SOURCE: она<eos>
GOLD: <sos>она
PRED: <sos>оа

SOURCE: подтвердила<eos>
GOLD: <sos>подтвердила
PRED: <sos>пдтвердила

SOURCE: новую<eos>
GOLD: <sos>новую
PRED: <sos>пвую

SOURCE: версию<eos>
GOLD: <sos>версию
PRED: <sos>врсию

SOURCE: Холл<eos>
GOLD: <sos>Холл
PRED: <sos>л л

SOURCE: Прикорневые<eos>
GOLD: <sos>Прикорневые
PRED: <sos>Пикорневые

SOURCE: листья<eos>
GOLD: <sos>листья
PRE

**Можно ли скзаать, почему модель ошибается?**

Можно выделить следующие случаи:
1. Модель не знает падеж слова (у неё вообще нет контекста) (девятое марта-девятого марта)
2. Есть похожее слово (провел-повел), которое модель знает и ставит его
3. Случаи, когда модель выдает несуществующее слово, являющееся опечаткой реального слова (допрос-ппрос, она-оа). Скорее всего, это можно исправить обучением большего количества эпох

**Сравните результаты всех разработанных моделей.**

Обучить модель с lstm не удалось (выше можно найти её плачевные результаты), а попробовать разные параметры attention и др. не успели

**Что помогло вам в выполнении работы**

Статья про seq2seq https://guillaumegenthial.github.io/sequence-to-sequence.html
в частности, трюк, который позволяет ускорять обучение

Был еще полезный ресурс: http://www.realworldnlpbook.com/blog/building-seq2seq-machine-translation-models-using-allennlp.html

**чего не хватало**

Времени

Нормального gpu

Документации и примеров использования allennlp


Лучшие Score'ы на Kaggle:

https://www.kaggle.com/submissions/15640962/15640962.raw Transformer + bilinear (Мультипликативное) attention


Private Score -- 0.91619

Public Score -- 0.91502



https://www.kaggle.com/submissions/15591854/15591854.raw Tranfsormer + dotproduct attention

Private Score -- 0.97055

Public Score -- 0.97153
